In [20]:
%load_ext autoreload
%autoreload 1

In [21]:
print(str(len(X_train)))


NameError: name 'X_train' is not defined

In [1]:
import pandas as pd
import matplotlib
import matplotlib.pyplot as plt

# Data Import

## Import

In [5]:
import os
import sys
nb_dir = os.path.split(os.getcwd())[0]
if nb_dir not in sys.path:
    sys.path.append(nb_dir)
    
from Import.CorpusImporter import CorpusImporter
corpus = CorpusImporter()

In [ ]:
corpus.clearMemory()
corpus.crawlNYT(per_tag=335, is_multilabel=False)

In [ ]:
print(str(len(corpus._Collection)) + " Artikel eingelesen.")

In [ ]:
corpus._Collection[3].tags

## Show Data Information

In [ ]:
def plotFreqDistAsBarChart(fdist,n, title, x, y):
    words = [x[0] for x in fdist.most_common(n)]
    values = [x[1] for x in fdist.most_common(n)]
    matplotlib.style.use('ggplot')
    
    d = {'values': values}
    df = pd.DataFrame(d)


    ax = df.plot(kind='bar',legend=False,title=title)
    ax.set_xticklabels(words)
    ax.set_xlabel(x,fontsize=12)
    ax.set_ylabel(y,fontsize=12)

    plt.show()

In [ ]:
from collections import Counter

tags = [text.tags[0] for text in corpus._Collection]
plotFreqDistAsBarChart(Counter(tags),20,"Number of Articles for Classes", "Class", "Number of Articles")

## Create Data Sets

In [ ]:
from sklearn.model_selection import train_test_split
X_train, X_test, Y_train, Y_test = train_test_split([news.text for news in corpus._Collection if news.text is not None], [news.tags[0] for news in corpus._Collection if news.text is not None], test_size=0.2, random_state=42)
print(len(X_train), " Newspaper Articles in the Training Set")
print(len(X_test), " Newspaper Articles in the Test Set")

## Data Exploration

In [ ]:
from Import.LinguisticVectorizer import LinguisticVectorizer
lv = LinguisticVectorizer()
ling_data = lv.transform(X_train)

In [ ]:
ling_df = pd.DataFrame(data=ling_data,columns=lv.get_feature_names())
print(ling_df.head())
ling_df.describe().transpose()

In [ ]:
import math
X_train_pd = pd.DataFrame(X_train)

In [ ]:
classes = ["Technology", "Arts", "Opinion", "Science", "Politics", "Sports", "Style", "Health", "Business"]
for kclass in classes:
    Y_train_pd_class = pd.DataFrame(Y_train) == kclass
    classd = [x[0] for x in X_train_pd[Y_train_pd_class].values.tolist() if isinstance(x[0], str)]
    classd_data = lv.transform(classd)
    class_ling_df = pd.DataFrame(data=classd_data,columns=lv.get_feature_names())
    print(kclass)
    print(class_ling_df.describe().transpose())

# Building The Pipeline

In [2]:
#%run Import/Preprocessor.py
#%run Import/LinguisticVectorizer.py
#%run Import/NamedEntityVectorizer.py
from Import.Preprocessor import Preprocessor
from Import.LinguisticVectorizer import LinguisticVectorizer
from Import.NamedEntityVectorizer import NamedEntityVectorizer

In [168]:
# Reset Imports

import sys
#del sys.modules['Import.Preprocessor']
del sys.modules['Import.LinguisticVectorizer']

#del sys.modules['Import.NamedEntityVectorizer']

In [55]:
del sys.modules['Import.CorpusImporter']

In [23]:
from Import.LinguisticVectorizer import LinguisticVectorizer

In [3]:
from sklearn.preprocessing import StandardScaler
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.naive_bayes import MultinomialNB
from sklearn.pipeline import Pipeline, FeatureUnion
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import FunctionTransformer
from sklearn.decomposition import PCA
from sklearn.linear_model import LogisticRegression
from sklearn.decomposition import TruncatedSVD
from nltk.corpus import stopwords
from nltk.stem.snowball import SnowballStemmer 
from nltk import PorterStemmer
from nltk import LancasterStemmer
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_classif

import numpy as np
import re
from collections import Counter

preprocessor = Preprocessor(stopwords = stopwords.words('english'), stemmer = SnowballStemmer("english"))

#[CV] features__ngram_tf_idf__counts__max_features=1868, features__ngram_tf_idf__counts__ngram_range=(1, 3), dim_red__n_components=1788, k_best__k=762 

# max_df = 0.75 for corpus-specific stopwords
cv = CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=2000, preprocessor=preprocessor.get_preprocessed_text)
tt = TfidfTransformer()
lv = LinguisticVectorizer()
clf = LogisticRegression(verbose=100)
pca = PCA(n_components=1200)

pv = NamedEntityVectorizer(max_features=100, entity="PERSON", stanford_tagger=False)

class SelectAtMostKBest(SelectKBest):
    def _check_params(self, X, y):
        print(X.shape)
        if not (self.k == "all" or 0 <= self.k <= X.shape[1]):
            self.k = "all"
            
select = SelectKBest(score_func=f_classif, k=1500)

fu = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', cv),
      ('tf_idf', tt)
    ])),
    ('lv', Pipeline([
      ('linguistic', lv)
    ]))
    #,('pv', Pipeline([
    #  ('person', pv)
    #]))
])

pipeline = Pipeline([
  ('features', fu),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler(with_mean=True)),
  ('k_best', select),
  ('dim_red', pca),
  ('classifier', clf)
])

# Training of Model

In [ ]:
pipeline.fit(X_train[:2], Y_train[:2])

In [ ]:
import datetime
with open("/home/retkowski/Debug/NER.log", "a") as myfile:
    myfile.write(datetime.datetime.now().strftime("%Y-%m-%d %H:%M:%S")+ " | "+ "Testlog" +"\n")

In [ ]:
score = pipeline.score(X_test[:5], Y_test[:5])

# Hypertuning

In [ ]:
from sklearn.externals.joblib import Parallel, parallel_backend, register_parallel_backend
import ipyparallel as ipp
from ipyparallel import Client
from ipyparallel.joblib import IPythonParallelBackend
import dill

ipp.register_joblib_backend()

c = Client()
print(c.ids)
bview = c.load_balanced_view()

# this is taken from the ipyparallel source code
register_parallel_backend('ipyparallel', lambda : IPythonParallelBackend(view=bview))

c[:].use_dill()

## Grid Search

In [ ]:
from sklearn.model_selection import GridSearchCV

param_grid = [
    {
       # 'k_best__k': [200,500,800,1000],
        'dim_red__n_components': [100, 500, 900, 1200],
       # 'features__ngram_tf_idf__counts__max_features': [500,800,1000,1200,1400],
        'features__ngram_tf_idf__counts__ngram_range': [(1,1),(1,2),(1,3)]
    }
]

grid = GridSearchCV(pipeline, cv=3, n_jobs=1, param_grid=param_grid, verbose=100, error_score=100)

#with parallel_backend('ipyparallel'):


In [ ]:
grid.fit(X_train, Y_train)

In [ ]:
c.clear()

## Randomized Search

In [ ]:
from sklearn.model_selection import RandomizedSearchCV
import scipy

param_dist = {
        'k_best__k': scipy.stats.randint(50, 1500),
        'dim_red__n_components': scipy.stats.randint(1000, 2000),
        'features__ngram_tf_idf__counts__max_features': scipy.stats.randint(1600, 2400),
        'features__ngram_tf_idf__counts__ngram_range': [(1,1),(1,2),(1,3)]
}

randsearch = RandomizedSearchCV(pipeline, cv=3, n_jobs=1, param_distributions=param_dist, verbose=100, error_score=100, n_iter=25)

#with parallel_backend('ipyparallel'):
randsearch.fit(X_train, Y_train)

In [ ]:
from pandas.tools.plotting import scatter_matrix

#print(map(list, randsearch.cv_results_['params']))

#print(randsearch.cv_results_['params'])
print(randsearch.cv_results_['params'][0])

dfx = pd.DataFrame([i for i in randsearch.cv_results_['params']])
dfx["accuracy"] = randsearch.cv_results_['mean_test_score']
#print(dfx.columns)
dfx.columns = ['n_components', 'max_features', 'n_gram', 'k_best', 'accuracy']
dfx["n_gram_min"], dfx["n_gram_max"] = zip(*dfx.n_gram) #dfx.ix[:, ['n_gram']]
print(dfx.sort_values(by="accuracy"))

scatter_matrix(dfx, diagonal='hist', c=dfx['accuracy'])
plt.show()

# Dimension Reduction

In [ ]:
plt.figure(1, figsize=(4, 3))
plt.clf()
plt.axes([.2, .2, .7, .7])
plt.plot(pca.explained_variance_, linewidth=2)
plt.axis('tight')
plt.xlabel('n_components')
plt.ylabel('explained_variance_')
plt.show()

In [170]:
%run Import/FeatureAnalyzer.py
import plotly
plotly.offline.init_notebook_mode() # run at the start of every ipython notebook
from time import time

import numpy as np
import matplotlib.pyplot as plt
from matplotlib import offsetbox
from sklearn import (manifold, datasets, decomposition, ensemble,
                     discriminant_analysis, random_projection)

xx = pipeline.fit_transform(X_train[:4000], Y_train[:4000])

#----------------------------------------------------------------------
# Scale and visualize the embedding vectors
def plot_embedding(X, title=None):
    x_min, x_max = np.min(X, 0), np.max(X, 0)
    X = (X - x_min) / (x_max - x_min)
    
    
    data = []

    for topic in list(set(Y_train)):
        data.append(
            Scatter(
                x = [x[0] for i, x in enumerate(X, 0) if topic == Y_train[i]],
                y = [x[1] for i, x in enumerate(X, 0) if topic == Y_train[i]],
                mode ="markers",
                name = topic)
        )
        layout = Layout(
            showlegend = True,
            title=title,
            xaxis = dict(
                title='Component 1',
            ),
            yaxis = dict(
                title='Component 2',
            ),
            hovermode = 'closest'
        )    

    fig = Figure(data=data, layout=layout)

    offline.iplot(fig)


print("Computing PCA projection")
t0 = time()
X_pca = decomposition.PCA(n_components=2).fit_transform(xx)
plot_embedding(X_pca,
               "Principal Components Projection of the Texts (Time %.2fs)" %
               (time() - t0))

# t-SNE embedding of the digits dataset
print("Computing t-SNE embedding")
tsne = manifold.TSNE(n_components=2, init='random',
                     perplexity = 30, learning_rate = 40,
                     n_iter = 5000, n_iter_without_progress = 200)
t0 = time()

#X_reduced = decomposition.PCA(n_components=50, random_state=0).fit_transform(xx)
X_tsne = tsne.fit_transform(xx)

plot_embedding(X_tsne,
               "t-SNE Embedding of the Texts (Time %.2fs)" %
               (time() - t0))

print("Computing t-SNE embedding")
tsne = manifold.TSNE(n_components=2, init='pca',
                     perplexity = 30, learning_rate = 300,
                     n_iter = 5000, n_iter_without_progress = 200)
t0 = time()

#X_reduced = decomposition.PCA(n_components=50, random_state=0).fit_transform(xx)
X_tsne = tsne.fit_transform(xx)

plot_embedding(X_tsne,
               "t-SNE Embedding of the Texts (Time %.2fs)" %
               (time() - t0))

print("Computing t-SNE embedding")
tsne = manifold.TSNE(n_components=2, init='random',
                     perplexity = 30, learning_rate = 300,
                     n_iter = 5000, n_iter_without_progress = 200)
t0 = time()

###

X_reduced = decomposition.PCA(n_components=100, random_state=0).fit_transform(xx)
X_tsne = tsne.fit_transform(X_reduced)

plot_embedding(X_tsne,
               "t-SNE Embedding of the Texts (Time %.2fs)" %
               (time() - t0))

print("Computing t-SNE embedding")
tsne = manifold.TSNE(n_components=2, init='random',
                     perplexity = 30, learning_rate = 300,
                     n_iter = 5000, n_iter_without_progress = 200)
t0 = time()



#X_reduced = decomposition.PCA(n_components=50, random_state=0).fit_transform(xx)
X_tsne = tsne.fit_transform(xx)

plot_embedding(X_tsne,
               "t-SNE Embedding of the Texts (Time %.2fs)" %
               (time() - t0))


# t-SNE embedding of the digits dataset
print("Computing t-SNE embedding")
tsne = manifold.TSNE(n_components=2, init='pca',
                     perplexity = 30, learning_rate = 40,
                     n_iter = 5000, n_iter_without_progress = 200)
t0 = time()

#X_reduced = decomposition.PCA(n_components=50, random_state=0).fit_transform(xx)
X_tsne = tsne.fit_transform(xx)

plot_embedding(X_tsne,
               "t-SNE Embedding of the Texts (Time %.2fs)" %
               (time() - t0))

print("Computing t-SNE embedding")
tsne = manifold.TSNE(n_components=2, init='pca',
                     perplexity = 30, learning_rate = 40,
                     n_iter = 5000, n_iter_without_progress = 200)
t0 = time()

X_reduced = decomposition.PCA(n_components=50, random_state=0).fit_transform(xx)
X_tsne = tsne.fit_transform(X_reduced)

plot_embedding(X_tsne,
               "t-SNE Embedding of the Texts (Time %.2fs)" %
               (time() - t0))

plt.show()


/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:113: UserWarning:

Features [2016] are constant.

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:114: RuntimeWarning:

invalid value encountered in true_divide



[LibLinear]Computing PCA projection


/opt/conda/lib/python3.5/site-packages/sklearn/utils/deprecation.py:70: DeprecationWarning:

Function transform is deprecated; Support to use estimators as feature selectors will be removed in version 0.19. Use SelectFromModel instead.



Computing t-SNE embedding


Computing t-SNE embedding


Computing t-SNE embedding


Computing t-SNE embedding


Computing t-SNE embedding


Computing t-SNE embedding


# Feature Selection

In [ ]:
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_classif
test = SelectKBest(score_func=f_classif, k="all")
fit = test.fit(fu.fit_transform(X_train), Y_train)

In [ ]:
scores_df = pd.DataFrame(data=[fit.scores_],columns=np.concatenate((cv.get_feature_names(), lv.get_feature_names())))
pd.set_option('display.max_rows', None)
scores_df.transpose().sort_values(by=[0], ascending=False)

In [ ]:
del sys.modules['Import.NamedEntityVectorizer']
from Import.NamedEntityVectorizer import NamedEntityVectorizer

In [ ]:
%%capture
#Discard that shit
from sklearn.feature_selection import chi2
test_chi = SelectKBest(score_func=chi2, k="all")
fit_chi = test_chi.fit(fu.fit_transform(X_train), Y_train)
#numpy.set_printoptions(precision=3)
#print(fit.scores_)
#features = fit.transform(X)

In [ ]:
nerv = NamedEntityVectorizer(entity="PERSON",max_features=4)

print(nerv.fit([X_train[0]]))

print(nerv.transform())

#import time
#start_time = time.time()
#print(nerv._stanford_tagger(X_train[0]))
#print("--- %s seconds ---" % (time.time() - start_time))

In [ ]:
scores_df = pd.DataFrame(data=[fit_chi.scores_],columns=np.concatenate((cv.get_feature_names(), lv.get_feature_names())))
pd.set_option('display.max_rows', None)
scores_df.transpose().sort_values(by=[0], ascending=False)

# Evaluation

In [ ]:
%run "Import/Evaluation.py"

In [ ]:
evaluation = Evaluation()
evaluation.print_probabilites(pipeline=pipeline, text="Internet does not like the climate change.")

In [ ]:
import pickle
with open('grid_pre.pickle', 'wb') as fp:
    pickle.dump(grid, fp)

# Data

In [6]:
corpus.clearMemory()

In [7]:
corpus.crawlNYT(per_tag=1001, is_multilabel=False, nytPaths = ["2007","2006","2005","2004","2003","2002","2001","2000","1999","1998","1997","1996","1995","1994"])

Maximum Documents:  9009
Reading archives [/home/retkowski/nltk_data/nyt/2007]:  ['01.tgz', '02.tgz', '03.tgz', '04.tgz', '05.tgz', '06.tgz']
Reading archives [/home/retkowski/nltk_data/nyt/2006]:  ['01.tgz', '02.tgz', '03.tgz', '04.tgz', '05.tgz', '06.tgz', '07.tgz', '08.tgz', '09.tgz', '10.tgz', '11.tgz', '12.tgz']
Reading archives [/home/retkowski/nltk_data/nyt/2005]:  ['01.tgz', '02.tgz', '03.tgz', '04.tgz', '05.tgz', '06.tgz', '07.tgz', '08.tgz', '09.tgz', '10.tgz', '11.tgz', '12.tgz']
Reading archives [/home/retkowski/nltk_data/nyt/2004]:  ['01.tgz', '02.tgz', '03.tgz', '04.tgz', '05.tgz', '06.tgz', '07.tgz', '08.tgz', '09.tgz', '10.tgz', '11.tgz', '12.tgz']
Reading archives [/home/retkowski/nltk_data/nyt/2003]:  ['01.tgz', '02.tgz', '03.tgz', '04.tgz', '05.tgz', '06.tgz', '07.tgz', '08.tgz', '09.tgz', '10.tgz', '11.tgz', '12.tgz']
Reading archives [/home/retkowski/nltk_data/nyt/2002]:  ['01.tgz', '02.tgz', '03.tgz', '04.tgz', '05.tgz', '06.tgz', '07.tgz', '08.tgz', '09.tgz', '10

In [8]:
print(str(len(corpus._Collection)) + " Artikel eingelesen.")
print(corpus._Collection[0].titles)

9006 Artikel eingelesen.
Categorized, Compared and Displayed: Social Ills as Museum Specimens
        


In [9]:
from sklearn.model_selection import train_test_split
X_train, X_test, Y_train, Y_test = train_test_split([news.text for news in corpus._Collection if news.text is not None], [news.tags[0] for news in corpus._Collection if news.text is not None], test_size=0.11, random_state=42)
print(len(X_train), " Newspaper Articles in the Training Set")
print(len(X_test), " Newspaper Articles in the Test Set")

8010  Newspaper Articles in the Training Set
991  Newspaper Articles in the Test Set


In [63]:
X_train_half = X_train[:4000]

In [64]:
Y_train_half = Y_train[:4000]

In [ ]:
%%capture
results = {}
for n_train in [50, 100, 200, 500, 1000, 2000, 4000, 8000]:
    print("Starten des Trainings für " + str(n_train))
    pipeline.fit(X_train[:n_train], Y_train[:n_train])
    print("Berechnung des Scores für " + str(n_train))
    score = pipeline.score(X_test, Y_test)
    print("Anzahl der Datensätze: " + str(n_train), ", Score: " + str(score))
    results[n_train] = score

In [171]:
print(results)

{2000: 0.80020181634712406, 1000: 0.78809283551967713, 50: 0.49243188698284562, 4000: 0.81634712411705346, 500: 0.7709384460141272, 200: 0.70534813319878908, 100: 0.58526740665993948, 8000: 0.8092835519677094}


In [222]:
preprocessor = Preprocessor(stopwords = stopwords.words('english'), stemmer = SnowballStemmer("english"))

#[CV] features__ngram_tf_idf__counts__max_features=1868, features__ngram_tf_idf__counts__ngram_range=(1, 3), dim_red__n_components=1788, k_best__k=762 

# max_df = 0.75 for corpus-specific stopwords
cv = CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=4000, preprocessor=preprocessor.get_preprocessed_text)
tt = TfidfTransformer()
lv = LinguisticVectorizer()
clf = LogisticRegression(verbose=100)
pca = PCA(n_components=1200)

pv = NamedEntityVectorizer(max_features=100, entity="PERSON", stanford_tagger=False)

class SelectAtMostKBest(SelectKBest):
    def _check_params(self, X, y):
        print(X.shape)
        if not (self.k == "all" or 0 <= self.k <= X.shape[1]):
            self.k = "all"
            
select = SelectKBest(score_func=f_classif, k=1500)

from sklearn import (neural_network)

clf = neural_network.MLPClassifier(hidden_layer_sizes=(300,300),solver='adam',activation='relu',learning_rate_init=0.01,max_iter=750,verbose=True)

mlp_pipeline = Pipeline([
  ('features', fu),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler(with_mean=True)),
  ('classifier', clf)
])

In [223]:
print(len(Y_train))

8010


In [224]:
mlp_pipeline.fit(X_train[:4000],Y_train[:4000])

Iteration 1, loss = 1.70573589
Iteration 2, loss = 0.17166751
Iteration 3, loss = 0.03159025
Iteration 4, loss = 0.01134120
Iteration 5, loss = 0.00840453
Iteration 6, loss = 0.00652073
Iteration 7, loss = 0.00267377
Iteration 8, loss = 0.00487711
Iteration 9, loss = 0.00454523
Iteration 10, loss = 0.00826610
Training loss did not improve more than tol=0.000100 for two consecutive epochs. Stopping.


Pipeline(steps=[('features', FeatureUnion(n_jobs=1,
       transformer_list=[('ngram_tf_idf', Pipeline(steps=[('counts', CountVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_featu...e=True, solver='adam', tol=0.0001, validation_fraction=0.1,
       verbose=True, warm_start=False))])

In [225]:
print("Hallo")

Hallo


In [226]:
mlp_pipeline.classes_

array(['Arts', 'Business', 'Health', 'Opinion', 'Politics', 'Science',
       'Sports', 'Style', 'Technology'], 
      dtype='<U10')

In [227]:
print(len(X_test))

991


In [228]:
score = mlp_pipeline.score(X_test, Y_test)

In [229]:
score

0.8173562058526741

In [230]:
# ohne MS/DR (200,200), 4000 Features: 83,6
# ohne MS/DR (200,200): 82,4
# ohne MS/DR (100,100): 82
# ohne MS/DR (1000,1000): 81
# mit MS/DR (200,200): 78

In [9]:
from Import.Preprocessor import Preprocessor
from Import.LinguisticVectorizer import LinguisticVectorizer

In [380]:
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier, VotingClassifier
from sklearn.naive_bayes import GaussianNB, MultinomialNB
from sklearn.neighbors import KNeighborsClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.svm import SVC

from sklearn.preprocessing import StandardScaler
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.naive_bayes import MultinomialNB
from sklearn.pipeline import Pipeline, FeatureUnion
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import FunctionTransformer
from sklearn.decomposition import PCA
from sklearn.linear_model import LogisticRegression
from sklearn.decomposition import TruncatedSVD
from nltk.corpus import stopwords
from nltk.stem.snowball import SnowballStemmer 
from nltk import PorterStemmer
from nltk import LancasterStemmer
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_classif

import numpy as np
import re
from collections import Counter

preprocessor = Preprocessor(stopwords = stopwords.words('english'), stemmer = SnowballStemmer("english"))
from sklearn import metrics

# Logistische Regression

In [496]:
fu = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=2000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ]))
])

logistic_pipeline = Pipeline([
  ('features', fu),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler(with_mean=True)),
  ('k_best', SelectKBest(score_func=f_classif, k=1500)),
  ('dim_red', PCA(n_components=1200)),
  ('classifier', LogisticRegression(verbose=100))
])

In [247]:
logistic_pipeline.fit(X_train[:4000],Y_train[:4000])

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:113: UserWarning:

Features [2016] are constant.

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:114: RuntimeWarning:

invalid value encountered in true_divide



[LibLinear]

Pipeline(steps=[('features', FeatureUnion(n_jobs=1,
       transformer_list=[('ngram_tf_idf', Pipeline(steps=[('counts', CountVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_featu...='l2', random_state=None, solver='liblinear', tol=0.0001,
          verbose=100, warm_start=False))])

In [248]:
log_predicted = logistic_pipeline.predict(X_test)

In [250]:
print(metrics.accuracy_score(Y_test, log_predicted))
print(metrics.classification_report(Y_test, log_predicted))
print(metrics.cohen_kappa_score(Y_test, log_predicted))
metrics.confusion_matrix(Y_test, log_predicted)

0.816347124117
             precision    recall  f1-score   support

       Arts       0.87      0.83      0.85       133
   Business       0.79      0.79      0.79        95
     Health       0.75      0.77      0.76       119
    Opinion       0.79      0.75      0.77       102
   Politics       0.82      0.87      0.84       112
    Science       0.76      0.71      0.73        99
     Sports       0.94      0.96      0.95       121
      Style       0.83      0.84      0.84       106
 Technology       0.78      0.80      0.79       104

avg / total       0.82      0.82      0.82       991

0.793104714054


array([[110,   4,   5,   3,   0,   3,   0,   5,   3],
       [  1,  75,   2,   1,   2,   1,   4,   4,   5],
       [  1,   1,  92,   2,   6,  10,   0,   2,   5],
       [  5,   2,   5,  77,   8,   1,   1,   1,   2],
       [  2,   4,   3,   4,  97,   0,   0,   1,   1],
       [  1,   0,  12,   4,   1,  70,   1,   3,   7],
       [  1,   0,   0,   2,   0,   1, 116,   0,   1],
       [  4,   4,   3,   1,   2,   3,   0,  89,   0],
       [  1,   5,   1,   4,   3,   3,   2,   2,  83]])

# Random Forest

In [251]:
fu = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=2000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ]))
])

random_ppl = Pipeline([
  ('features', fu),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler(with_mean=True)),
  ('k_best', SelectKBest(score_func=f_classif, k=1500)),
  ('dim_red', PCA(n_components=1200)),
  ('classifier', RandomForestClassifier(verbose=100))
])

In [ ]:
random_ppl.fit(X_train[:4000],Y_train[:4000])

In [ ]:
random_predicted = random_ppl.predict(X_test) 

In [267]:
print(metrics.accuracy_score(Y_test, random_predicted))
print(metrics.classification_report(Y_test, random_predicted))
print(metrics.cohen_kappa_score(Y_test, random_predicted))
metrics.confusion_matrix(Y_test, random_predicted)

0.60141271443
             precision    recall  f1-score   support

       Arts       0.61      0.74      0.67       133
   Business       0.50      0.59      0.54        95
     Health       0.52      0.60      0.55       119
    Opinion       0.42      0.39      0.41       102
   Politics       0.66      0.59      0.62       112
    Science       0.62      0.57      0.59        99
     Sports       0.90      0.84      0.87       121
      Style       0.76      0.57      0.65       106
 Technology       0.45      0.45      0.45       104

avg / total       0.61      0.60      0.60       991

0.550609718297


array([[ 98,   6,   3,   6,   1,   4,   1,   5,   9],
       [  9,  56,   4,   8,   3,   6,   0,   1,   8],
       [  3,   6,  71,   8,   6,  10,   3,   3,   9],
       [ 10,  11,  15,  40,  12,   0,   1,   1,  12],
       [  5,   6,  10,  12,  66,   3,   2,   3,   5],
       [  9,   8,  12,   2,   0,  56,   0,   3,   9],
       [  2,   2,   4,   2,   6,   1, 102,   1,   1],
       [ 15,   3,   9,   4,   2,   7,   2,  60,   4],
       [ 10,  13,   9,  13,   4,   4,   2,   2,  47]])

In [494]:
fu = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=2000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ]))
])

random_200_ppl = Pipeline([
  ('features', fu),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler(with_mean=True)),
  ('k_best', SelectKBest(score_func=f_classif, k=1500)),
  ('dim_red', PCA(n_components=1200)),
  ('classifier', RandomForestClassifier(verbose=100, n_estimators=200))
])

In [312]:
random_200_ppl.fit(X_train[:4000],Y_train[:4000])

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:113: UserWarning:

Features [2016] are constant.

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:114: RuntimeWarning:

invalid value encountered in true_divide



building tree 1 of 200
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.2s remaining:    0.0s
building tree 2 of 200
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.4s remaining:    0.0s
building tree 3 of 200
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.5s remaining:    0.0s
building tree 4 of 200
[Parallel(n_jobs=1)]: Done   4 out of   4 | elapsed:    0.6s remaining:    0.0s
building tree 5 of 200
[Parallel(n_jobs=1)]: Done   5 out of   5 | elapsed:    0.7s remaining:    0.0s
building tree 6 of 200
[Parallel(n_jobs=1)]: Done   6 out of   6 | elapsed:    0.8s remaining:    0.0s
building tree 7 of 200
[Parallel(n_jobs=1)]: Done   7 out of   7 | elapsed:    0.9s remaining:    0.0s
building tree 8 of 200
[Parallel(n_jobs=1)]: Done   8 out of   8 | elapsed:    1.0s remaining:    0.0s
building tree 9 of 200
[Parallel(n_jobs=1)]: Done   9 out of   9 | elapsed:    1.1s remaining:    0.0s
building tree 10 of 200
[Parallel(n_jobs=1)]: Done  10 out of  10 | elaps

Pipeline(steps=[('features', FeatureUnion(n_jobs=1,
       transformer_list=[('ngram_tf_idf', Pipeline(steps=[('counts', CountVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_featu...tors=200, n_jobs=1, oob_score=False, random_state=None,
            verbose=100, warm_start=False))])

In [313]:
random_200_predicted = random_200_ppl.predict(X_test) 

[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   4 out of   4 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   5 out of   5 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   6 out of   6 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   7 out of   7 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   8 out of   8 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   9 out of   9 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  10 out of  10 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  11 out of  11 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  12 out of  12 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  13 out of  1

In [314]:
print(metrics.accuracy_score(Y_test, random_200_predicted))
print(metrics.classification_report(Y_test, random_200_predicted))
print(metrics.cohen_kappa_score(Y_test, random_200_predicted))
metrics.confusion_matrix(Y_test, random_200_predicted)

0.818365287588
             precision    recall  f1-score   support

       Arts       0.90      0.84      0.87       133
   Business       0.79      0.83      0.81        95
     Health       0.80      0.80      0.80       119
    Opinion       0.77      0.65      0.70       102
   Politics       0.77      0.85      0.81       112
    Science       0.77      0.74      0.75        99
     Sports       0.97      0.95      0.96       121
      Style       0.80      0.89      0.84       106
 Technology       0.76      0.79      0.77       104

avg / total       0.82      0.82      0.82       991

0.795419357058


array([[112,   3,   1,   3,   0,   3,   0,  11,   0],
       [  1,  79,   3,   4,   0,   0,   0,   3,   5],
       [  0,   3,  95,   3,   4,   9,   1,   2,   2],
       [  2,   3,   8,  66,  16,   1,   1,   1,   4],
       [  1,   2,   2,   5,  95,   2,   0,   2,   3],
       [  2,   3,   6,   3,   1,  73,   0,   1,  10],
       [  1,   1,   1,   0,   0,   0, 115,   2,   1],
       [  5,   3,   1,   0,   0,   2,   0,  94,   1],
       [  1,   3,   2,   2,   7,   5,   1,   1,  82]])

In [ ]:
fu = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=2000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ]))
])

random_1000_ppl = Pipeline([
  ('features', fu),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler(with_mean=True)),
  ('k_best', SelectKBest(score_func=f_classif, k=1500)),
  ('dim_red', PCA(n_components=1200)),
  ('classifier', RandomForestClassifier(verbose=100, n_estimators=1000))
])

In [ ]:
random_1000_ppl.fit(X_train[:4000],Y_train[:4000])

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:113: UserWarning:

Features [2016] are constant.

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:114: RuntimeWarning:

invalid value encountered in true_divide



building tree 1 of 1000
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.2s remaining:    0.0s
building tree 2 of 1000
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.3s remaining:    0.0s
building tree 3 of 1000
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.4s remaining:    0.0s
building tree 4 of 1000
[Parallel(n_jobs=1)]: Done   4 out of   4 | elapsed:    0.5s remaining:    0.0s
building tree 5 of 1000
[Parallel(n_jobs=1)]: Done   5 out of   5 | elapsed:    0.6s remaining:    0.0s
building tree 6 of 1000
[Parallel(n_jobs=1)]: Done   6 out of   6 | elapsed:    0.8s remaining:    0.0s
building tree 7 of 1000
[Parallel(n_jobs=1)]: Done   7 out of   7 | elapsed:    0.9s remaining:    0.0s
building tree 8 of 1000
[Parallel(n_jobs=1)]: Done   8 out of   8 | elapsed:    1.0s remaining:    0.0s
building tree 9 of 1000
[Parallel(n_jobs=1)]: Done   9 out of   9 | elapsed:    1.1s remaining:    0.0s
building tree 10 of 1000
[Parallel(n_jobs=1)]: Done  10 out of  

In [ ]:
random_1000_predicted = random_1000_ppl.predict(X_test) 

[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   4 out of   4 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   5 out of   5 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   6 out of   6 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   7 out of   7 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   8 out of   8 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   9 out of   9 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  10 out of  10 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  11 out of  11 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  12 out of  12 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  13 out of  1

In [ ]:
print(metrics.accuracy_score(Y_test, random_1000_predicted))
print(metrics.classification_report(Y_test, random_1000_predicted))
print(metrics.cohen_kappa_score(Y_test, random_1000_predicted))
metrics.confusion_matrix(Y_test, random_1000_predicted)

0.811301715439
             precision    recall  f1-score   support

       Arts       0.90      0.82      0.86       133
   Business       0.77      0.83      0.80        95
     Health       0.81      0.80      0.80       119
    Opinion       0.76      0.61      0.67       102
   Politics       0.75      0.89      0.82       112
    Science       0.78      0.73      0.75        99
     Sports       0.98      0.93      0.95       121
      Style       0.78      0.89      0.83       106
 Technology       0.76      0.78      0.77       104

avg / total       0.81      0.81      0.81       991

0.787491471197


array([[109,   2,   1,   3,   0,   5,   0,  12,   1],
       [  1,  79,   2,   3,   0,   0,   1,   4,   5],
       [  0,   2,  95,   2,   5,   8,   0,   3,   4],
       [  5,   5,   8,  62,  18,   1,   0,   1,   2],
       [  0,   3,   2,   3, 100,   1,   0,   1,   2],
       [  1,   4,   6,   3,   1,  72,   0,   2,  10],
       [  0,   1,   1,   4,   0,   0, 112,   2,   1],
       [  4,   3,   2,   0,   0,   2,   0,  94,   1],
       [  1,   4,   1,   2,   9,   3,   1,   2,  81]])

# Naiver Bayes

In [ ]:
fu = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=2000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ]))
])

nb_ppl = Pipeline([
  ('features', fu),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler(with_mean=True)),
  ('k_best', SelectKBest(score_func=f_classif, k=1500)),
  ('dim_red', PCA(n_components=1200)),
  ('classifier', GaussianNB())
])

In [ ]:
nb_ppl.fit(X_train[:4000],Y_train[:4000])

In [ ]:
nb_predicted = nb_ppl.predict(X_test) 

In [268]:
print(metrics.accuracy_score(Y_test, nb_predicted))
print(metrics.classification_report(Y_test, nb_predicted))
print(metrics.cohen_kappa_score(Y_test, nb_predicted))
metrics.confusion_matrix(Y_test, nb_predicted)

0.604439959637
             precision    recall  f1-score   support

       Arts       0.60      0.72      0.65       133
   Business       0.85      0.42      0.56        95
     Health       0.55      0.50      0.52       119
    Opinion       0.53      0.38      0.45       102
   Politics       0.43      0.70      0.53       112
    Science       0.60      0.67      0.63        99
     Sports       0.97      0.77      0.86       121
      Style       0.68      0.59      0.63       106
 Technology       0.53      0.62      0.57       104

avg / total       0.64      0.60      0.61       991

0.553786141907


array([[96,  2, 12,  1, 10,  4,  1,  5,  2],
       [11, 40,  4,  9,  9,  3,  1,  6, 12],
       [ 4,  0, 59,  2, 24, 19,  0,  4,  7],
       [ 9,  0,  7, 39, 22,  9,  0,  3, 13],
       [ 8,  1,  6,  8, 78,  2,  0,  0,  9],
       [ 4,  0,  9,  2,  7, 66,  0,  2,  9],
       [ 6,  0,  1,  6,  6,  1, 93,  5,  3],
       [19,  0,  4,  1, 14,  2,  0, 63,  3],
       [ 4,  4,  5,  5, 11,  4,  1,  5, 65]])

In [492]:
fu = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=2000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ]))
])

mnb_ppl = Pipeline([
  ('features', fu),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', MinMaxScaler()),
  ('k_best', SelectKBest(score_func=f_classif, k=1500)),
  ('dim_red', PCA(n_components=1200)),
  ('scaler2', MinMaxScaler()),
  ('classifier', MultinomialNB())
])

In [ ]:
mnb_ppl.fit(X_train[:4000],Y_train[:4000])

In [ ]:
mnb_predicted = mnb_ppl.predict(X_test) 

In [321]:
print(metrics.accuracy_score(Y_test, mnb_predicted))
print(metrics.classification_report(Y_test, mnb_predicted))
print(metrics.cohen_kappa_score(Y_test, mnb_predicted))
metrics.confusion_matrix(Y_test, mnb_predicted)

0.810292633703
             precision    recall  f1-score   support

       Arts       0.90      0.78      0.84       133
   Business       0.81      0.74      0.77        95
     Health       0.71      0.87      0.78       119
    Opinion       0.92      0.64      0.75       102
   Politics       0.78      0.89      0.83       112
    Science       0.87      0.72      0.78        99
     Sports       0.98      0.94      0.96       121
      Style       0.66      0.94      0.78       106
 Technology       0.80      0.73      0.76       104

avg / total       0.83      0.81      0.81       991

0.78622758957


array([[104,   3,   3,   1,   2,   2,   0,  17,   1],
       [  1,  70,   5,   1,   1,   2,   0,  11,   4],
       [  2,   1, 103,   0,   4,   5,   0,   1,   3],
       [  3,   3,  11,  65,  11,   1,   1,   6,   1],
       [  1,   2,   4,   2, 100,   0,   0,   1,   2],
       [  0,   0,  11,   1,   3,  71,   0,   6,   7],
       [  1,   1,   1,   1,   0,   0, 114,   2,   1],
       [  3,   2,   1,   0,   0,   0,   0, 100,   0],
       [  0,   4,   6,   0,   8,   1,   1,   8,  76]])

# Nearest Neighbors

In [ ]:
fu = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=2000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ]))
])

nn_ppl = Pipeline([
  ('features', fu),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler(with_mean=True)),
  ('k_best', SelectKBest(score_func=f_classif, k=1500)),
  ('dim_red', PCA(n_components=1200)),
  ('classifier', KNeighborsClassifier(n_neighbors=7))
])

In [ ]:
nn_ppl.fit(X_train[:4000],Y_train[:4000])

In [ ]:
nn_predicted = nn_ppl.predict(X_test) 

In [269]:
print(metrics.accuracy_score(Y_test, nn_predicted))
print(metrics.classification_report(Y_test, nn_predicted))
print(metrics.cohen_kappa_score(Y_test, nn_predicted))
metrics.confusion_matrix(Y_test, nn_predicted)

0.380423814329
             precision    recall  f1-score   support

       Arts       0.93      0.10      0.18       133
   Business       0.32      0.53      0.40        95
     Health       0.80      0.33      0.46       119
    Opinion       0.80      0.04      0.07       102
   Politics       0.80      0.60      0.68       112
    Science       0.93      0.14      0.25        99
     Sports       0.96      0.62      0.75       121
      Style       0.16      0.79      0.27       106
 Technology       0.46      0.30      0.36       104

avg / total       0.70      0.38      0.39       991

0.305633566548


array([[ 13,  16,   0,   0,   0,   0,   0, 100,   4],
       [  0,  50,   0,   0,   0,   0,   1,  42,   2],
       [  0,  15,  39,   0,   2,   0,   0,  53,  10],
       [  0,  10,   2,   4,  12,   0,   0,  70,   4],
       [  0,   6,   4,   1,  67,   0,   0,  31,   3],
       [  0,  19,   3,   0,   0,  14,   1,  54,   8],
       [  0,   8,   0,   0,   0,   0,  75,  36,   2],
       [  1,  16,   0,   0,   0,   1,   0,  84,   4],
       [  0,  14,   1,   0,   3,   0,   1,  54,  31]])

In [275]:
fu = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=2000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ]))
])

nn_20_ppl = Pipeline([
  ('features', fu),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler(with_mean=True)),
  ('k_best', SelectKBest(score_func=f_classif, k=1500)),
  ('dim_red', PCA(n_components=1200)),
  ('classifier', KNeighborsClassifier(n_neighbors=20))
])

In [ ]:
nn_20_ppl.fit(X_train[:4000],Y_train[:4000])

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:113: UserWarning:

Features [2016] are constant.

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:114: RuntimeWarning:

invalid value encountered in true_divide



Pipeline(steps=[('features', FeatureUnion(n_jobs=1,
       transformer_list=[('ngram_tf_idf', Pipeline(steps=[('counts', CountVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_featu...wski',
           metric_params=None, n_jobs=1, n_neighbors=20, p=2,
           weights='uniform'))])

In [ ]:
nn_20_predicted = nn_20_ppl.predict(X_test) 

In [ ]:
print(metrics.accuracy_score(Y_test, nn_20_predicted))
print(metrics.classification_report(Y_test, nn_20_predicted))
print(metrics.cohen_kappa_score(Y_test, nn_20_predicted))
metrics.confusion_matrix(Y_test, nn_20_predicted)

0.410696266398
             precision    recall  f1-score   support

       Arts       1.00      0.03      0.06       133
   Business       0.68      0.66      0.67        95
     Health       0.85      0.34      0.49       119
    Opinion       1.00      0.01      0.02       102
   Politics       0.80      0.59      0.68       112
    Science       1.00      0.14      0.25        99
     Sports       0.98      0.70      0.82       121
      Style       0.17      0.95      0.28       106
 Technology       0.60      0.31      0.41       104

avg / total       0.79      0.41      0.41       991

0.339130395064


array([[  4,   2,   0,   0,   0,   0,   0, 123,   4],
       [  0,  63,   0,   0,   0,   0,   0,  31,   1],
       [  0,   5,  41,   0,   2,   0,   1,  64,   6],
       [  0,   5,   4,   1,  12,   0,   0,  79,   1],
       [  0,   3,   2,   0,  66,   0,   0,  40,   1],
       [  0,   1,   1,   0,   0,  14,   0,  76,   7],
       [  0,   1,   0,   0,   0,   0,  85,  35,   0],
       [  0,   4,   0,   0,   0,   0,   0, 101,   1],
       [  0,   9,   0,   0,   3,   0,   1,  59,  32]])

In [ ]:
fu = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=2000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ]))
])

nn_50_ppl = Pipeline([
  ('features', fu),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler(with_mean=True)),
  ('k_best', SelectKBest(score_func=f_classif, k=1500)),
  ('dim_red', PCA(n_components=1200)),
  ('classifier', KNeighborsClassifier(n_neighbors=50))
])

In [ ]:
nn_50_ppl.fit(X_train[:4000],Y_train[:4000])

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:113: UserWarning:

Features [2016] are constant.

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:114: RuntimeWarning:

invalid value encountered in true_divide



Pipeline(steps=[('features', FeatureUnion(n_jobs=1,
       transformer_list=[('ngram_tf_idf', Pipeline(steps=[('counts', CountVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_featu...wski',
           metric_params=None, n_jobs=1, n_neighbors=50, p=2,
           weights='uniform'))])

In [ ]:
nn_50_predicted = nn_50_ppl.predict(X_test) 

In [ ]:
print(metrics.accuracy_score(Y_test, nn_50_predicted))
print(metrics.classification_report(Y_test, nn_50_predicted))
print(metrics.cohen_kappa_score(Y_test, nn_50_predicted))
metrics.confusion_matrix(Y_test, nn_50_predicted)

0.529767911201
             precision    recall  f1-score   support

       Arts       1.00      0.06      0.11       133
   Business       0.55      0.83      0.66        95
     Health       0.72      0.66      0.68       119
    Opinion       1.00      0.02      0.04       102
   Politics       0.69      0.76      0.72       112
    Science       0.94      0.16      0.28        99
     Sports       0.97      0.85      0.91       121
      Style       0.24      0.94      0.39       106
 Technology       0.74      0.52      0.61       104

avg / total       0.77      0.53      0.49       991

0.472169836121


array([[  8,   7,   1,   0,   1,   0,   1, 112,   3],
       [  0,  79,   1,   0,   0,   0,   1,  11,   3],
       [  0,   6,  78,   0,   2,   0,   0,  31,   2],
       [  0,  18,  11,   2,  22,   1,   0,  44,   4],
       [  0,  10,   4,   0,  85,   0,   0,  13,   0],
       [  0,   6,  14,   0,   3,  16,   0,  55,   5],
       [  0,   1,   0,   0,   0,   0, 103,  16,   1],
       [  0,   5,   0,   0,   0,   0,   0, 100,   1],
       [  0,  11,   0,   0,  11,   0,   1,  27,  54]])

In [305]:
fu = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=2000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ]))
])

nn_100_ppl = Pipeline([
  ('features', fu),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler(with_mean=True)),
  ('k_best', SelectKBest(score_func=f_classif, k=1500)),
  ('dim_red', PCA(n_components=1200)),
  ('classifier', KNeighborsClassifier(n_neighbors=100))
])

In [306]:
nn_100_ppl.fit(X_train[:4000],Y_train[:4000])

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:113: UserWarning:

Features [2016] are constant.

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:114: RuntimeWarning:

invalid value encountered in true_divide



Pipeline(steps=[('features', FeatureUnion(n_jobs=1,
       transformer_list=[('ngram_tf_idf', Pipeline(steps=[('counts', CountVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_featu...ski',
           metric_params=None, n_jobs=1, n_neighbors=100, p=2,
           weights='uniform'))])

In [307]:
nn_100_predicted = nn_100_ppl.predict(X_test) 

In [308]:
print(metrics.accuracy_score(Y_test, nn_100_predicted))
print(metrics.classification_report(Y_test, nn_100_predicted))
print(metrics.cohen_kappa_score(Y_test, nn_100_predicted))
metrics.confusion_matrix(Y_test, nn_100_predicted)

0.587285570131
             precision    recall  f1-score   support

       Arts       1.00      0.10      0.18       133
   Business       0.71      0.78      0.74        95
     Health       0.34      0.96      0.50       119
    Opinion       0.00      0.00      0.00       102
   Politics       0.65      0.87      0.74       112
    Science       1.00      0.26      0.42        99
     Sports       0.98      0.93      0.95       121
      Style       0.52      0.87      0.65       106
 Technology       0.79      0.52      0.63       104

avg / total       0.68      0.59      0.53       991

0.534716147681


/opt/conda/lib/python3.5/site-packages/sklearn/metrics/classification.py:1113: UndefinedMetricWarning:

Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.



array([[ 13,   7,  65,   0,   4,   0,   0,  42,   2],
       [  0,  74,  10,   0,   0,   0,   0,   6,   5],
       [  0,   2, 114,   0,   2,   0,   0,   1,   0],
       [  0,   5,  48,   0,  33,   0,   1,  13,   2],
       [  0,   3,  10,   0,  97,   0,   0,   1,   1],
       [  0,   3,  51,   0,   2,  26,   0,  14,   3],
       [  0,   1,   6,   0,   0,   0, 112,   1,   1],
       [  0,   3,  11,   0,   0,   0,   0,  92,   0],
       [  0,   6,  25,   0,  11,   0,   1,   7,  54]])

# SVM

In [ ]:
fu = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=2000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ]))
])

svc_ppl = Pipeline([
  ('features', fu),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler(with_mean=True)),
  ('k_best', SelectKBest(score_func=f_classif, k=1500)),
  ('dim_red', PCA(n_components=1200)),
  ('classifier', SVC(kernel='rbf', probability=True, verbose=100))
])

In [ ]:
svc_ppl.fit(X_train[:4000],Y_train[:4000])

In [ ]:
svc_predicted = svc_ppl.predict(X_test) 

In [270]:
print(metrics.accuracy_score(Y_test, svc_predicted))
print(metrics.classification_report(Y_test, svc_predicted))
print(metrics.cohen_kappa_score(Y_test, svc_predicted))
metrics.confusion_matrix(Y_test, svc_predicted)

0.847628657921
             precision    recall  f1-score   support

       Arts       0.90      0.86      0.88       133
   Business       0.82      0.83      0.83        95
     Health       0.83      0.81      0.82       119
    Opinion       0.83      0.79      0.81       102
   Politics       0.82      0.88      0.85       112
    Science       0.76      0.75      0.75        99
     Sports       0.97      0.98      0.98       121
      Style       0.89      0.88      0.88       106
 Technology       0.79      0.81      0.80       104

avg / total       0.85      0.85      0.85       991

0.828365989533


array([[115,   3,   0,   4,   2,   3,   0,   6,   0],
       [  1,  79,   1,   2,   0,   3,   1,   3,   5],
       [  0,   2,  96,   2,   4,  10,   1,   1,   3],
       [  4,   3,   6,  81,   7,   1,   0,   0,   0],
       [  1,   3,   2,   4,  99,   1,   0,   0,   2],
       [  2,   1,   7,   3,   0,  74,   0,   0,  12],
       [  0,   1,   0,   0,   0,   1, 119,   0,   0],
       [  4,   2,   2,   1,   0,   3,   0,  93,   1],
       [  1,   2,   1,   1,   9,   2,   2,   2,  84]])

In [322]:
fu = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=2000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ]))
])

svc_low_ppl = Pipeline([
  ('features', fu),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler(with_mean=True)),
  ('k_best', SelectKBest(score_func=f_classif, k=1500)),
  ('dim_red', PCA(n_components=1200)),
  ('classifier', SVC(kernel='rbf', probability=True, verbose=100, C=0.001))
])

In [ ]:
svc_low_ppl.fit(X_train[:4000],Y_train[:4000])

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:113: UserWarning:

Features [2016] are constant.

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:114: RuntimeWarning:

invalid value encountered in true_divide



[LibSVM]

Pipeline(steps=[('features', FeatureUnion(n_jobs=1,
       transformer_list=[('ngram_tf_idf', Pipeline(steps=[('counts', CountVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_featu...bf',
  max_iter=-1, probability=True, random_state=None, shrinking=True,
  tol=0.001, verbose=100))])

In [ ]:
svc_low_predicted = svc_low_ppl.predict(X_test) 

In [ ]:
print(metrics.accuracy_score(Y_test, svc_low_predicted))
print(metrics.classification_report(Y_test, svc_low_predicted))
print(metrics.cohen_kappa_score(Y_test, svc_low_predicted))
metrics.confusion_matrix(Y_test, svc_low_predicted)

0.106962663976
             precision    recall  f1-score   support

       Arts       0.00      0.00      0.00       133
   Business       0.00      0.00      0.00        95
     Health       0.00      0.00      0.00       119
    Opinion       0.00      0.00      0.00       102
   Politics       0.00      0.00      0.00       112
    Science       0.00      0.00      0.00        99
     Sports       0.00      0.00      0.00       121
      Style       0.11      1.00      0.19       106
 Technology       0.00      0.00      0.00       104

avg / total       0.01      0.11      0.02       991

0.0


/opt/conda/lib/python3.5/site-packages/sklearn/metrics/classification.py:1113: UndefinedMetricWarning:

Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.



array([[  0,   0,   0,   0,   0,   0,   0, 133,   0],
       [  0,   0,   0,   0,   0,   0,   0,  95,   0],
       [  0,   0,   0,   0,   0,   0,   0, 119,   0],
       [  0,   0,   0,   0,   0,   0,   0, 102,   0],
       [  0,   0,   0,   0,   0,   0,   0, 112,   0],
       [  0,   0,   0,   0,   0,   0,   0,  99,   0],
       [  0,   0,   0,   0,   0,   0,   0, 121,   0],
       [  0,   0,   0,   0,   0,   0,   0, 106,   0],
       [  0,   0,   0,   0,   0,   0,   0, 104,   0]])

In [489]:
fu = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=2000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ]))
])

svc_high_ppl = Pipeline([
  ('features', fu),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler(with_mean=True)),
  ('k_best', SelectKBest(score_func=f_classif, k=1500)),
  ('dim_red', PCA(n_components=1200)),
  ('classifier', SVC(kernel='rbf', probability=True, verbose=100, C=1000))
])

In [172]:
lvvvv = LinguisticVectorizer()

In [173]:
lvvvv.transform(X_train[:1])

array([[  1.09400000e+03,   1.20000000e+01,   2.37826087e+01,
          4.58226691e+00,   2.50457038e-01,   1.38939671e-01,
          1.84643510e-01,   2.74223035e-03,   0.00000000e+00,
          3.65630713e-03,   2.10237660e-02,   1.10000000e+01,
          4.37842779e-01,   2.96190476e-01,   3.10786106e-01,
          5.70621469e-01,   0.00000000e+00,   0.00000000e+00,
          0.00000000e+00,   0.00000000e+00,   0.00000000e+00,
          4.91773309e-01,   9.14076782e-04,   3.60866079e-02]])

In [ ]:
svc_high_ppl.fit(X_train[:4000],Y_train[:4000])

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:113: UserWarning:

Features [2020] are constant.

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:114: RuntimeWarning:

invalid value encountered in true_divide



[LibSVM]

Pipeline(steps=[('features', FeatureUnion(n_jobs=1,
       transformer_list=[('ngram_tf_idf', Pipeline(steps=[('counts', CountVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_featu...bf',
  max_iter=-1, probability=True, random_state=None, shrinking=True,
  tol=0.001, verbose=100))])

In [178]:
svc_high_predicted = svc_high_ppl.predict(X_test) 

In [179]:
print(metrics.accuracy_score(Y_test, svc_high_predicted))
print(metrics.classification_report(Y_test, svc_high_predicted))
print(metrics.cohen_kappa_score(Y_test, svc_high_predicted))
metrics.confusion_matrix(Y_test, svc_high_predicted)

0.851664984864
             precision    recall  f1-score   support

       Arts       0.89      0.87      0.88       133
   Business       0.81      0.85      0.83        95
     Health       0.85      0.82      0.83       119
    Opinion       0.80      0.80      0.80       102
   Politics       0.85      0.88      0.86       112
    Science       0.77      0.75      0.76        99
     Sports       0.97      0.98      0.98       121
      Style       0.89      0.87      0.88       106
 Technology       0.79      0.82      0.80       104

avg / total       0.85      0.85      0.85       991

0.832920826146


array([[116,   4,   0,   5,   0,   3,   0,   5,   0],
       [  1,  81,   1,   2,   0,   2,   1,   3,   4],
       [  0,   2,  97,   2,   4,   9,   1,   1,   3],
       [  4,   3,   5,  82,   6,   1,   0,   0,   1],
       [  2,   3,   2,   4,  98,   1,   0,   0,   2],
       [  1,   1,   7,   4,   0,  74,   0,   0,  12],
       [  1,   1,   0,   0,   0,   0, 119,   0,   0],
       [  4,   2,   1,   2,   0,   4,   0,  92,   1],
       [  1,   3,   1,   1,   7,   2,   2,   2,  85]])

In [356]:
fu = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=4000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ]))
])

svc_high_without_ppl = Pipeline([
  ('features', fu),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler(with_mean=True)),
  ('classifier', SVC(kernel='rbf', probability=False, verbose=100, C=1000))
])

In [359]:
svc_high_without_ppl.fit(X_train[:4000],Y_train[:4000])

[LibSVM]

Pipeline(steps=[('features', FeatureUnion(n_jobs=1,
       transformer_list=[('ngram_tf_idf', Pipeline(steps=[('counts', CountVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_featu...bf',
  max_iter=-1, probability=True, random_state=None, shrinking=True,
  tol=0.001, verbose=100))])

In [360]:
svc_high_without_predicted = svc_high_without_ppl.predict(X_test) 

In [176]:
print(metrics.accuracy_score(Y_test, svc_high_without_predicted))
print(metrics.classification_report(Y_test, svc_high_without_predicted))
print(metrics.cohen_kappa_score(Y_test, svc_high_without_predicted))
metrics.confusion_matrix(Y_test, svc_high_without_predicted)

NameError: name 'svc_high_without_predicted' is not defined

In [ ]:
fu = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=4000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ]))
])

svc_very_high_ppl = Pipeline([
  ('features', fu),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler(with_mean=True)),
  ('k_best', SelectKBest(score_func=f_classif, k=1500)),
  ('dim_red', PCA(n_components=1200)),
  ('classifier', SVC(kernel='rbf', probability=False, verbose=100, C=10000))
])

In [ ]:
svc_very_high_ppl.fit(X_train[:4000],Y_train[:4000])

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:113: UserWarning:

Features [4016] are constant.

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:114: RuntimeWarning:

invalid value encountered in true_divide



[LibSVM]

Pipeline(steps=[('features', FeatureUnion(n_jobs=1,
       transformer_list=[('ngram_tf_idf', Pipeline(steps=[('counts', CountVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_featu...f',
  max_iter=-1, probability=False, random_state=None, shrinking=True,
  tol=0.001, verbose=100))])

In [ ]:
svc_very_high_predicted = svc_very_high_ppl.predict(X_test) 

In [ ]:
print(metrics.accuracy_score(Y_test, svc_very_high_predicted))
print(metrics.classification_report(Y_test, svc_very_high_predicted))
print(metrics.cohen_kappa_score(Y_test, svc_very_high_predicted))
metrics.confusion_matrix(Y_test, svc_very_high_predicted)

0.848637739657
             precision    recall  f1-score   support

       Arts       0.87      0.89      0.88       133
   Business       0.76      0.82      0.79        95
     Health       0.84      0.76      0.80       119
    Opinion       0.88      0.82      0.85       102
   Politics       0.80      0.90      0.85       112
    Science       0.81      0.82      0.81        99
     Sports       0.96      0.97      0.96       121
      Style       0.88      0.87      0.87       106
 Technology       0.82      0.76      0.79       104

avg / total       0.85      0.85      0.85       991

0.829482298393


array([[119,   3,   0,   0,   3,   1,   0,   7,   0],
       [  1,  78,   1,   2,   0,   3,   2,   2,   6],
       [  2,   6,  90,   3,   5,   7,   1,   1,   4],
       [  4,   1,   4,  84,   8,   1,   0,   0,   0],
       [  2,   3,   2,   2, 101,   1,   0,   0,   1],
       [  2,   2,   6,   0,   1,  81,   0,   1,   6],
       [  0,   0,   1,   2,   0,   0, 117,   1,   0],
       [  6,   2,   1,   1,   0,   4,   0,  92,   0],
       [  1,   7,   2,   2,   8,   2,   2,   1,  79]])

In [ ]:
fu = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=4000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ]))
])

svc_low_high_ppl = Pipeline([
  ('features', fu),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler(with_mean=True)),
  ('k_best', SelectKBest(score_func=f_classif, k=1500)),
  ('dim_red', PCA(n_components=1200)),
  ('classifier', SVC(kernel='rbf', probability=False, verbose=100, C=100))
])

In [ ]:
svc_low_high_ppl.fit(X_train[:4000],Y_train[:4000])

MemoryError: 

In [ ]:
svc_low_high_predicted = svc_low_high_ppl.predict(X_test) 

In [ ]:
print(metrics.accuracy_score(Y_test, svc_low_high_predicted))
print(metrics.classification_report(Y_test, svc_low_high_predicted))
print(metrics.cohen_kappa_score(Y_test, svc_low_high_predicted))
metrics.confusion_matrix(Y_test, svc_low_high_predicted)

In [334]:
svc_high_ppl

Pipeline(steps=[('features', FeatureUnion(n_jobs=1,
       transformer_list=[('ngram_tf_idf', Pipeline(steps=[('counts', CountVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_featu...bf',
  max_iter=-1, probability=True, random_state=None, shrinking=True,
  tol=0.001, verbose=100))])

In [335]:
svc_low_ppl

Pipeline(steps=[('features', FeatureUnion(n_jobs=1,
       transformer_list=[('ngram_tf_idf', Pipeline(steps=[('counts', CountVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_featu...bf',
  max_iter=-1, probability=True, random_state=None, shrinking=True,
  tol=0.001, verbose=100))])

In [337]:
svc_high_predicted

array(['Technology', 'Arts', 'Arts', 'Politics', 'Business', 'Science',
       'Health', 'Style', 'Opinion', 'Arts', 'Politics', 'Arts', 'Opinion',
       'Health', 'Technology', 'Sports', 'Sports', 'Science', 'Technology',
       'Health', 'Politics', 'Business', 'Technology', 'Science',
       'Business', 'Opinion', 'Technology', 'Politics', 'Science',
       'Science', 'Arts', 'Politics', 'Politics', 'Science', 'Science',
       'Opinion', 'Technology', 'Opinion', 'Arts', 'Sports', 'Business',
       'Business', 'Politics', 'Politics', 'Style', 'Opinion', 'Arts',
       'Business', 'Arts', 'Arts', 'Style', 'Arts', 'Politics',
       'Technology', 'Arts', 'Sports', 'Arts', 'Style', 'Business',
       'Technology', 'Technology', 'Science', 'Science', 'Business',
       'Arts', 'Politics', 'Health', 'Science', 'Technology', 'Sports',
       'Technology', 'Opinion', 'Science', 'Arts', 'Style', 'Health',
       'Arts', 'Arts', 'Science', 'Arts', 'Arts', 'Technology', 'Arts',
       'Arts

# Perceptron

In [490]:
fu = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=4000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ]))
])

from sklearn import neural_network

clf = neural_network.MLPClassifier(hidden_layer_sizes=(300,300),solver='adam',activation='relu',learning_rate_init=0.01,max_iter=750,verbose=True)

mlp1_pipeline = Pipeline([
  ('features', fu),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler(with_mean=True)),
  ('classifier', clf)
])

In [302]:
mlp1_pipeline.fit(X_train[:4000],Y_train[:4000])

Iteration 1, loss = 1.60780146
Iteration 2, loss = 0.10881438
Iteration 3, loss = 0.01942552
Iteration 4, loss = 0.00532681
Iteration 5, loss = 0.00393073
Iteration 6, loss = 0.00336272
Iteration 7, loss = 0.00382100
Iteration 8, loss = 0.00294462
Iteration 9, loss = 0.00168502
Iteration 10, loss = 0.00154445
Iteration 11, loss = 0.00153442
Iteration 12, loss = 0.00152781
Iteration 13, loss = 0.00152286
Training loss did not improve more than tol=0.000100 for two consecutive epochs. Stopping.


Pipeline(steps=[('features', FeatureUnion(n_jobs=1,
       transformer_list=[('ngram_tf_idf', Pipeline(steps=[('counts', CountVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_featu...e=True, solver='adam', tol=0.0001, validation_fraction=0.1,
       verbose=True, warm_start=False))])

In [303]:
mlp1_predicted = mlp1_pipeline.predict(X_test) 

In [304]:
print(metrics.accuracy_score(Y_test, mlp1_predicted))
print(metrics.classification_report(Y_test, mlp1_predicted))
print(metrics.cohen_kappa_score(Y_test, mlp1_predicted))
metrics.confusion_matrix(Y_test, mlp1_predicted)

0.828456104945
             precision    recall  f1-score   support

       Arts       0.87      0.86      0.87       133
   Business       0.79      0.76      0.77        95
     Health       0.84      0.79      0.81       119
    Opinion       0.79      0.82      0.80       102
   Politics       0.83      0.84      0.84       112
    Science       0.79      0.77      0.78        99
     Sports       0.94      0.96      0.95       121
      Style       0.78      0.86      0.82       106
 Technology       0.78      0.76      0.77       104

avg / total       0.83      0.83      0.83       991

0.806755028418


array([[115,   1,   0,   2,   2,   3,   0,   9,   1],
       [  2,  72,   1,   5,   0,   1,   3,   7,   4],
       [  1,   4,  94,   4,   4,   9,   1,   1,   1],
       [  4,   2,   4,  84,   5,   0,   0,   0,   3],
       [  1,   3,   3,   4,  94,   1,   0,   2,   4],
       [  2,   1,   5,   3,   2,  76,   0,   3,   7],
       [  0,   1,   1,   1,   0,   0, 116,   1,   1],
       [  4,   2,   2,   1,   0,   3,   2,  91,   1],
       [  3,   5,   2,   3,   6,   3,   1,   2,  79]])

# Entscheidungsbaum

In [296]:
from sklearn.tree import DecisionTreeClassifier

In [297]:
fu = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=2000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ]))
])

dtree_ppl = Pipeline([
  ('features', fu),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler(with_mean=True)),
  ('k_best', SelectKBest(score_func=f_classif, k=1500)),
  ('dim_red', PCA(n_components=1200)),
  ('classifier', DecisionTreeClassifier())
])

In [298]:
dtree_ppl.fit(X_train[:4000],Y_train[:4000])

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:113: UserWarning:

Features [2016] are constant.

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:114: RuntimeWarning:

invalid value encountered in true_divide



Pipeline(steps=[('features', FeatureUnion(n_jobs=1,
       transformer_list=[('ngram_tf_idf', Pipeline(steps=[('counts', CountVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_featu...it=2, min_weight_fraction_leaf=0.0,
            presort=False, random_state=None, splitter='best'))])

In [299]:
dtree_predicted = dtree_ppl.predict(X_test) 

In [300]:
print(metrics.accuracy_score(Y_test, dtree_predicted))
print(metrics.classification_report(Y_test, dtree_predicted))
print(metrics.cohen_kappa_score(Y_test, dtree_predicted))
metrics.confusion_matrix(Y_test, dtree_predicted)

0.584258324924
             precision    recall  f1-score   support

       Arts       0.67      0.59      0.63       133
   Business       0.63      0.61      0.62        95
     Health       0.53      0.58      0.56       119
    Opinion       0.40      0.41      0.41       102
   Politics       0.61      0.65      0.63       112
    Science       0.58      0.51      0.54        99
     Sports       0.84      0.72      0.77       121
      Style       0.58      0.56      0.57       106
 Technology       0.45      0.61      0.52       104

avg / total       0.60      0.58      0.59       991

0.531914796047


array([[78,  3, 10,  4,  4,  7,  2, 15, 10],
       [ 2, 58,  3,  8,  5,  1,  3,  5, 10],
       [ 3,  5, 69, 12,  5, 10,  3,  3,  9],
       [ 5,  7, 11, 42, 12,  3,  4,  5, 13],
       [ 2,  5,  5, 12, 73,  0,  1,  2, 12],
       [ 6,  1, 12,  6,  6, 50,  2,  6, 10],
       [ 3,  3,  8,  2,  8,  2, 87,  3,  5],
       [13,  4,  4, 11,  1,  6,  1, 59,  7],
       [ 4,  6,  7,  7,  5,  7,  1,  4, 63]])

# Voting Classifier

In [497]:
eclf = VotingClassifier(estimators=[('word2vec', w2v_svc_ppl), ('svm',svc_high_ppl),('mlp',mlp1_pipeline),('nb', mnb_ppl), ('rf', random_200_ppl), ('lr', logistic_pipeline)], voting='soft', weights=[4,2,2,1,1,1])

In [ ]:
eclf.fit(X_train,Y_train)

[LibSVM]

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:113: UserWarning:

Features [2020] are constant.

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:114: RuntimeWarning:

invalid value encountered in true_divide



In [ ]:
eclf_predicted = eclf.predict(X_test) 

In [ ]:
for e in eclf.estimators:
    print(e)

In [502]:
print(metrics.accuracy_score(Y_test, eclf_predicted))
print(metrics.classification_report(Y_test, eclf_predicted))
print(metrics.cohen_kappa_score(Y_test, eclf_predicted))
metrics.confusion_matrix(Y_test, eclf_predicted)

0.887991927346
             precision    recall  f1-score   support

       Arts       0.92      0.90      0.91       133
   Business       0.82      0.82      0.82        95
     Health       0.89      0.89      0.89       119
    Opinion       0.86      0.87      0.86       102
   Politics       0.88      0.92      0.90       112
    Science       0.86      0.84      0.85        99
     Sports       0.97      0.97      0.97       121
      Style       0.89      0.95      0.92       106
 Technology       0.86      0.80      0.83       104

avg / total       0.89      0.89      0.89       991

0.873824282411


array([[120,   3,   0,   1,   2,   3,   0,   4,   0],
       [  1,  78,   1,   3,   0,   2,   1,   3,   6],
       [  0,   1, 106,   2,   3,   6,   0,   1,   0],
       [  4,   1,   4,  89,   3,   1,   0,   0,   0],
       [  1,   2,   3,   3, 103,   0,   0,   0,   0],
       [  2,   1,   3,   2,   1,  83,   0,   0,   7],
       [  0,   1,   0,   2,   0,   0, 117,   1,   0],
       [  2,   2,   0,   0,   0,   0,   1, 101,   0],
       [  0,   6,   2,   2,   5,   2,   1,   3,  83]])

In [504]:
eclf.predict_proba(["This is not very good"])

[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   4 out of   4 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   5 out of   5 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   6 out of   6 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   7 out of   7 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   8 out of   8 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   9 out of   9 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  10 out of  10 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  11 out of  11 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  12 out of  12 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  13 out of  1

array([[ 0.04978249,  0.05239954,  0.02882267,  0.50591169,  0.02343574,
         0.03635617,  0.02565079,  0.24540427,  0.03223665]])

In [509]:
import dill

In [ ]:
with open('eclf.pickle', 'wb') as handle:
    dill.dump(eclf, handle, protocol=dill.HIGHEST_PROTOCOL)

# $\chi^2$ Selektor

In [40]:
from sklearn.feature_selection import chi2,SelectKBest
from sklearn.preprocessing import MinMaxScaler

In [52]:
fu_chi = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=2000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ]))
])

chi2_ppl = None
chi2_ppl = Pipeline([
  ('features', fu_chi),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', MinMaxScaler()),
  ('k_best', SelectKBest(score_func=chi2, k="all")),
])

2020 Features analyzed

In [ ]:
chi2_ppl.fit(X_train[:4000],Y_train[:4000])

In [219]:
print(len(chi2_ppl.named_steps['k_best'].scores_))
print(chi2_ppl.named_steps['k_best'].scores_[:1])

2020
[ 9.93719203]


In [210]:
print(len(chi2_ppl.named_steps['features'].transformer_list[0][1].steps[0][1].get_feature_names()))

2000


In [227]:
chi2_data = []
chi2_i = 0

# Bitte weitergehen, hier gibt es nichts zu sehen
for feature_name in chi2_ppl.named_steps['features'].transformer_list[0][1].steps[0][1].get_feature_names() :
    chi2_data.append([feature_name, chi2_ppl.named_steps['k_best'].scores_[chi2_i]])
    chi2_i += 1
for feature_name in chi2_ppl.named_steps['features'].transformer_list[1][1].steps[0][1].get_feature_names() :
    chi2_data.append([feature_name, chi2_ppl.named_steps['k_best'].scores_[chi2_i]])
    chi2_i += 1

df_chi2 = pd.DataFrame(chi2_data)



In [ ]:
chi2_data = None

In [217]:
df_chi2.to_csv("/home/retkowski/chi2.csv")

In [247]:
from Import.FeatureAnalyzer import FeatureAnalyzer
from sklearn.preprocessing import MaxAbsScaler

In [245]:
x_chi_trans = fu_chi.fit(X_train[:4000]).transform(X_train[:4000])

In [275]:
scaler = StandardScaler(with_mean=True)
x_chi_scale = []

In [254]:
chi_feature_names = []
for feature_name in chi2_ppl.named_steps['features'].transformer_list[0][1].steps[0][1].get_feature_names() :
    chi_feature_names.append(feature_name)
for feature_name in chi2_ppl.named_steps['features'].transformer_list[1][1].steps[0][1].get_feature_names() :
    chi_feature_names.append(feature_name)


In [272]:
print(chi_feature_names[2019])

number_of_first_person_pronouns


In [305]:
chi_featureanalyzer = FeatureAnalyzer(topics=['Arts', 'Business', 'Science', 'Sports', 'Technology', 'Health', 'Opinion', 'Style', 'Politics'],
                                      feature_names=chi_feature_names)

In [263]:
chi_transformer = FunctionTransformer(lambda x: x.todense(), accept_sparse=True)

In [291]:
x_chi_transformed = None
x_chi_transformed = scaler.fit_transform(chi_transformer.fit_transform(x_chi_trans))

In [308]:
print(x_chi_transformed[0])

[-0.15840411 -0.23232527  1.86641655 ..., -1.51285894 -0.24235526
  0.94509398]


In [388]:
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
offline.init_notebook_mode(connected=True)
chi_featureanalyzer.clear_data()
chi_featureanalyzer.set_data(x_chi_transformed,Y_train[:4000])

In [389]:
chi_featureanalyzer.draw_violins()

In [317]:
iplot([{"x": [1, 2, 3], "y": [3, 1, 6]}])

In [228]:
FeatureAnalyzer.set_data(x_data=[data[1] for data in chi2_data], y_data=[data[0] for data in chi2_data])

TypeError: set_data() missing 1 required positional argument: 'self'

# ANOVA

In [220]:
from sklearn.feature_selection import f_classif,SelectKBest
from sklearn.preprocessing import MinMaxScaler

In [222]:
fu_anova = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=2000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ]))
])

anova_ppl = None
anova_ppl = Pipeline([
  ('features', fu_anova),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler()),
  ('k_best', SelectKBest(score_func=f_classif, k="all")),
])

In [224]:
anova_data = []
anova_i = 0

# Bitte weitergehen, hier gibt es nichts zu sehen
for feature_name in anova_ppl.named_steps['features'].transformer_list[0][1].steps[0][1].get_feature_names() :
    anova_data.append([feature_name, anova_ppl.named_steps['k_best'].scores_[anova_i]])
    anova_i += 1
for feature_name in anova_ppl.named_steps['features'].transformer_list[1][1].steps[0][1].get_feature_names() :
    anova_data.append([feature_name, anova_ppl.named_steps['k_best'].scores_[anova_i]])
    anova_i += 1

df_anova = pd.DataFrame(anova_data)

anova_data = None

df_anova.to_csv("/home/retkowski/anova.csv")

In [223]:
anova_ppl.fit(X_train[:4000],Y_train[:4000])

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:113: UserWarning:

Features [2020] are constant.

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:114: RuntimeWarning:

invalid value encountered in true_divide



Pipeline(steps=[('features', FeatureUnion(n_jobs=1,
       transformer_list=[('ngram_tf_idf', Pipeline(steps=[('counts', CountVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_featu...range=(0, 1))), ('k_best', SelectKBest(k='all', score_func=<function f_classif at 0x7f523029f6a8>))])

# Select from Model

In [3]:
from sklearn.feature_selection import SelectFromModel

In [2]:
fu_rfe = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=2000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ]))
])

clf = SVC(kernel='rbf', probability=True, verbose=100, C = 1000)
rf_feature_imp = RandomForestClassifier(200)


rfe_ppl = Pipeline([
  ('features', fu_rfe),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler())#,
  #('sfm', SelectFromModel(rf_feature_imp, threshold=0)),
  #('classifier', clf)
])  

NameError: name 'FeatureUnion' is not defined

In [366]:
#sfm = SelectFromModel(clf, threshold=0)
rf_feature_imp.fit(rfe_ppl.fit_transform(X_train[:4000]), Y_train[:4000])

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=None, max_features='auto', max_leaf_nodes=None,
            min_impurity_split=1e-07, min_samples_leaf=1,
            min_samples_split=2, min_weight_fraction_leaf=0.0,
            n_estimators=200, n_jobs=1, oob_score=False, random_state=None,
            verbose=0, warm_start=False)

In [371]:
random_data = []
random_i = 0

for feature_name in rfe_ppl.named_steps['features'].transformer_list[0][1].steps[0][1].get_feature_names() :
    random_data.append([feature_name, rf_feature_imp.feature_importances_[random_i]])
    random_i += 1
for feature_name in rfe_ppl.named_steps['features'].transformer_list[1][1].steps[0][1].get_feature_names() :
    random_data.append([feature_name, rf_feature_imp.feature_importances_[random_i]])
    random_i += 1

df_random = pd.DataFrame(random_data)

df_random.to_csv("/home/retkowski/random.csv")

In [379]:
print(rf_feature_imp.feature_importances_)

[  9.59952364e-05   2.21909892e-04   3.66668676e-04 ...,   3.96057614e-03
   7.50957579e-03   2.98875245e-03]


In [380]:
rf_feature_imp

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=None, max_features='auto', max_leaf_nodes=None,
            min_impurity_split=1e-07, min_samples_leaf=1,
            min_samples_split=2, min_weight_fraction_leaf=0.0,
            n_estimators=200, n_jobs=1, oob_score=False, random_state=None,
            verbose=0, warm_start=False)

In [ ]:
rf

# RFE

In [1]:
from sklearn.pipeline import FeatureUnion, Pipeline
from sklearn.feature_extraction.text import TfidfTransformer, CountVectorizer
from sklearn.feature_selection import RFE
from sklearn.svm import SVR
from Import.CorpusImporter import CorpusImporter
from Import.CrawlerImporter import CrawlerImporter
from Import.Preprocessor import Preprocessor
from Import.LinguisticVectorizer import LinguisticVectorizer
from Import.NamedEntityVectorizer import NamedEntityVectorizer
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import FunctionTransformer

# nltk
from nltk.corpus import stopwords
from nltk.stem.snowball import SnowballStemmer 
from nltk import PorterStemmer, LancasterStemmer


# Numpy
import numpy as np
import re
from collections import Counter

preprocessor = Preprocessor(stopwords = stopwords.words('english'), stemmer = SnowballStemmer("english"))
fu_rfee = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=2000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ]))
])

estimator = SVR(kernel="linear")
#selector = RFE(estimator, None, step=1)

rfee_ppl = Pipeline([
  ('features', fu_rfee),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler()),
  #('sfm', SelectFromModel(rf_feature_imp, threshold=0)),
  ('rfe', RFE(estimator, None, step=1))
])  

In [3]:
import os
import dill
corpus_file = './corpus.pickle'
Collection = []
if os.path.isfile(corpus_file):
    with open(corpus_file, 'rb') as handle:
        Collection = dill.load(handle)

from sklearn.model_selection import train_test_split
X_train, X_test, Y_train, Y_test = train_test_split([news.text for news in Collection if news.text is not None], [news.tags[0] for news in Collection if news.text is not None], test_size=0.11, random_state=42)

In [4]:
Y_train_label = list(set(Y_train))
Y_train_num = [Y_train_label.index(label) for label in Y_train]

In [6]:
print(Y_train_num[:100])

[2, 7, 4, 5, 6, 6, 8, 5, 7, 0, 5, 1, 3, 2, 1, 8, 0, 4, 2, 5, 6, 3, 8, 1, 4, 4, 7, 4, 0, 3, 8, 2, 4, 0, 7, 5, 3, 6, 6, 4, 6, 7, 3, 6, 2, 4, 4, 3, 8, 1, 5, 2, 2, 2, 7, 0, 4, 0, 3, 3, 6, 4, 1, 1, 6, 5, 4, 0, 2, 1, 0, 4, 1, 6, 5, 3, 7, 6, 4, 8, 2, 0, 5, 0, 4, 1, 1, 6, 1, 3, 1, 3, 8, 0, 6, 5, 4, 2, 3, 6]


In [ ]:
rfee_ppl.fit(X_train[:4000], Y_train_num[:4000])

In [ ]:
print(rfee_ppl)

# Hypertuning

In [ ]:
#
#
#clf = make_pipeline(StandardScaler(), 
#                    GridSearchCV(LogisticRegression(),
#                                 param_grid={'logisticregression__C': [0.1, 10.]},
#                                 cv=2,
#                                 refit=True))

#clf.fit()
#clf.predict()

In [ ]:
print("Test")

In [65]:
# PCA: Explained Variance Ratio, large portion of variance
# pca = PCA()
# pca.fit(X)
# cumsum = np.cumsum(pca.explained_variance_ratio_)
# d = np.argmax(cumsum >= 0.95) + 1

# pca = PCA(n_components=0.95)
# X_reduced = pca.fit_transform(X)

# Kernel PCA?
# CART-Formel

# Fehler untersuchen
#cl_a, cl_b = 3, 5

print(list(eclf_predicted[:3]))
print(type(Y_test[:2]))

X_aa = X_test[(Y_test == "Technology") & (list(eclf_predicted) == "Politics")]
#X_ab = X_train[(y_train == cl_a) & (y_train_pred == cl_b)]
#X_ba = X_train[(y_train == cl_b) & (y_train_pred == cl_a)]
#X_bb = X_train[(y_train == cl_b) & (y_train_pred == cl_b)]

['Technology', 'Arts', 'Arts']
<class 'list'>


In [69]:
(Y_test == "Technology") & (list(eclf_predicted) == "Politics")

False

In [77]:
print(len(list(eclf_predicted)))
len([Y_test == "Technology"])

991


1

In [507]:
xxa = [x for i, x in enumerate(X_test) if (Y_test[i] == "Technology") & (list(eclf_predicted)[i] == "Politics")]
print(xxa[1])

eclf.predict_proba([xxa[0]])


        For the first time since his abduction, a British reporter kidnapped in Gaza on March 12 was shown Friday in a video released to an Islamic militant Web site. Later on Friday, Israeli troops killed two young Palestinians and wounded a third near the Gaza border with Israel.
        The three Palestinians, ages 12, 13 and 16, were crouched near the border fence close to the demolished Israeli settlement of Dugit, said an army spokeswoman, Maj. Avital Leibovich. The three ''were walking in operational mode close to the fence, where we have alerts about infiltration,'' she said. ''We identified them as youth, not as children.''
        The three ignored warnings and were shot.
        The two youngest, Ahmed Abu Zubeida, 12, and Zaher al-Majdalawi, 13, were killed, Palestinian medical workers said. The third was wounded and taken to an Israeli hospital. The army said the boys had been planting what appeared to be an explosive device and might have been paid by elders to do so. Lo

array([[ 0.01521303,  0.01935262,  0.01688741,  0.01897541,  0.64182679,
         0.01761178,  0.01183928,  0.01521888,  0.2430748 ]])

In [101]:
[x for x in corpus._Collection if x.title == "Poverty Rate Falls Sharply Among Hispanics, Study Shows"]

AttributeError: 'Item' object has no attribute 'title'

# Word2Vec

In [82]:
from sklearn.ensemble import ExtraTreesClassifier
from sklearn.svm import SVC

In [128]:
print(len(word2vec.index2word))

400000


In [468]:
import gensim

word2vec = gensim.models.KeyedVectors.load_word2vec_format(os.getcwd() + "/../Word2Vec/glove_model2.txt", binary=False)
word2vec.init_sims(replace=True)

In [ ]:
# Keyerror if not found !!!

In [80]:
print(len(w2v.items()))

400000


In [344]:
print(len(word2vec["epidemic"]))

300


In [315]:
fu_w2v = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=2000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ]))
])

fu_w2v_pure = FeatureUnion([
    ('w2v_mean', Pipeline([
        ("word2vec vectorizer", MeanEmbeddingVectorizer(w2v)), 
        ("extra trees", ExtraTreesClassifier(n_estimators=9))
    ]))
])


w2v_ppl = Pipeline([
  ('features', fu_w2v_pure),
  #('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True))#,
  ('scaler', StandardScaler())#,
  #('sfm', SelectFromModel(rf_feature_imp, threshold=0)),
  #('classifier', clf)
])  

In [36]:
w2v_ppl.fit(X_train[:10],Y_train[:10])

Pipeline(steps=[('features', FeatureUnion(n_jobs=1,
       transformer_list=[('w2v_mean', Pipeline(steps=[('word2vec vectorizer', <__main__.MeanEmbeddingVectorizer object at 0x7f9b4d781780>), ('extra trees', ExtraTreesClassifier(bootstrap=False, class_weight=None, criterion='gini',
           max_depth=None, max_features='auto', max_leaf_nodes=None,
       ...mators=9, n_jobs=1, oob_score=False, random_state=None,
           verbose=0, warm_start=False))]))],
       transformer_weights=None))])

In [442]:
#X_title = [text.titles for text in corpus._Collection if len(text.titles) > 50 and len(text.titles) < 100]
#Y_title = [text.tags[0] for text in corpus._Collection if len(text.titles) > 50 and len(text.titles) < 100]
min_length=35
from sklearn.model_selection import train_test_split
X_title_train, X_title_test, Y_title_train, Y_title_test = train_test_split([news.titles for news in corpus._Collection if news.titles is not None], [news.tags[0] for news in corpus._Collection if news.titles is not None], test_size=0.2, random_state=42)

print(len(X_title_train))
print(len(X_title_test))

7204
1802


In [412]:
print(X_title_train)

['Martin Trow, 80, Sociologist And Higher Education Expert\n        ', 'In Mexico, Diabetes Strains Lives and Budgets\n        ', 'Katharine Bailey, Albert Francke\n      ', 'Roommates, the Online Version\n        ', 'Face Transplant Recipient Takes Outings and Blends In, Doctors Say\n        ', 'Georgia Tornado Strips Area of Medical Services\n        ', 'Some Buyers Grow Web-Weary, And Online Sales Lose Steam\n        ', 'Eloquent Tongues but Anguished Irish Hearts\n        ', 'FROM THE DESK OF DAVID POGUE: Asking the Crowd to Spread the News\n      ', 'Funeral Home Webcast Allows Out-of-Town Mourners to Pay Respects\n      ', "Edward Wright, Who Unearthed Ancient Boats on England's Coast, Dies at 82\n      ", 'House Votes to Bolster Database on Gun Buyers\n        ', 'A Fleeting Victory in Somalia\n        ', 'White House Gears Up to Sell Plan for Troop Increase in Iraq\n        ', 'Revamping At Airbus Is Delayed\n        ', 'As the Flattery Flies: A Buzzology Primer\n        ', 'Sc

In [431]:
from operator import itemgetter
count_stop = {}
for text in [text for i, text in enumerate(X_train) if Y_train[i] == "Opinion"]:
    for word in text.lower().strip().split(' '):
        if word in stopwords.words('english'):
            count_stop[word] = count_stop.get(word,0) + 1
print(sorted(count_stop.items(), key=itemgetter(1)))

[('theirs', 1), ('d', 1), ('s', 1), ('hers', 2), ('ours', 3), ('yours', 3), ('y', 3), ('don', 3), ('yourself', 6), ('haven', 11), ('herself', 13), ('below', 15), ('ourselves', 26), ('above', 35), ('myself', 36), ('won', 37), ('whom', 49), ('itself', 59), ('themselves', 66), ('himself', 67), ('again', 72), ('nor', 74), ('further', 77), ('here', 108), ('doing', 114), ('having', 133), ('am', 134), ('until', 141), ('each', 145), ('once', 146), ('during', 165), ('down', 194), ('off', 200), ('does', 218), ('between', 224), ('few', 227), ('under', 230), ('same', 231), ('him', 231), ('very', 234), ('too', 234), ('why', 234), ('re', 250), ('me', 256), ('before', 258), ('both', 259), ('did', 266), ('own', 274), ('being', 276), ('then', 281), ('through', 287), ('such', 290), ('against', 290), ('your', 322), ('while', 340), ('where', 341), ('she', 404), ('them', 410), ('over', 414), ('her', 430), ('any', 437), ('now', 455), ('after', 478), ('because', 484), ('how', 499), ('those', 511), ('just', 5

In [428]:
count_dic = {}
for tag in Y_train:
    count_dic[tag] = count_dic.get(tag,0) + 1
print(count_dic)

{'Technology': 897, 'Politics': 889, 'Science': 899, 'Health': 882, 'Business': 905, 'Opinion': 898, 'Style': 893, 'Arts': 867, 'Sports': 880}


In [452]:
print(len(X_title_train))
print(len(X_title_test))

print(len(X_train))
print(len(X_test))

7204
1802
8010
991


In [469]:
class MeanEmbeddingVectorizer(object):
    def __init__(self, word2vec):
        self.word2vec = word2vec
        # if a text is empty we should return a vector of zeros
        # with the same dimensionality as all the other vectors
        self.dim = 300
        self.stopwordsList = stopwords.words('english')
    
    def fit(self, X, y):
        return self
    
    def _remove_stopwords(self, document):
        return [word for word in document if word not in self.stopwordsList]
    
    def _mean(self, X):     
        return np.mean([self.word2vec[w] for w in self._remove_stopwords(X.lower().strip().split(' ')) if w in self.word2vec] 
                    or [np.zeros(self.dim)], axis=0)
    
    
    def transform(self, documents):         
        return np.array(
            [self._mean(d) for d in documents]
        )
    
w2v_fu = FeatureUnion([
    ("word2vec vectorizer", MeanEmbeddingVectorizer(word2vec))
])

w2v_svc_ppl = Pipeline([
  ('features', w2v_fu),
  #('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler(with_mean=True)),
  #('k_best', SelectKBest(score_func=f_classif, k=1500)),
  #('dim_red', PCA(n_components=1200)),
  ('classifier', SVC(kernel='rbf', probability=True, verbose=100, C = 1000))
])

In [1]:
import dill
with open('corpus.pickle', 'wb') as handle:
cocorpus.py.pyy.pyill.dump(corpus, handle, protocol=dill.HIGHEST_PROTOCOL)

NameError: name 'corpus' is not defined

In [365]:
print(len(X_train))

8010


In [347]:
print(word2vec.most_similar("epidemic"))

[('epidemics', 0.6823053359985352), ('Aids_epidemic', 0.6696153879165649), ('AIDS_epidemic', 0.6601665616035461), ('HIV_AIDS_epidemic', 0.6482120156288147), ('pandemic', 0.6384391784667969), ('epidemic_proportions', 0.6240929961204529), ('HIV_Aids_epidemic', 0.6149376630783081), ('scourge', 0.6077061891555786), ('outbreak', 0.6065651774406433), ('HIV_AIDS_pandemic', 0.5971630811691284)]


In [363]:
w2v_svc_ppl.predict_proba(["Clinton"])

array([[ 0.04122981,  0.1102639 ,  0.02572894,  0.14523611,  0.04535857,
         0.02410316,  0.04724034,  0.51367639,  0.04716277]])

In [470]:
w2v_svc_ppl.fit(X_title_train, Y_title_train)
w2v_svc_ppl.score(X_title_test,Y_title_test)
w2v_predict = w2v_svc_ppl.predict(X_title_test)
print(metrics.accuracy_score(Y_title_test, w2v_predict))
print(metrics.classification_report(Y_title_test, w2v_predict))
print(metrics.cohen_kappa_score(Y_title_test, w2v_predict))
metrics.confusion_matrix(Y_title_test, w2v_predict)

[LibSVM]0.617092119867
             precision    recall  f1-score   support

       Arts       0.58      0.55      0.57       215
   Business       0.59      0.61      0.60       200
     Health       0.64      0.71      0.67       209
    Opinion       0.47      0.51      0.49       189
   Politics       0.80      0.72      0.76       212
    Science       0.65      0.58      0.61       208
     Sports       0.68      0.68      0.68       198
      Style       0.57      0.65      0.61       187
 Technology       0.59      0.53      0.56       184

avg / total       0.62      0.62      0.62      1802

0.569163771336


array([[118,  10,  11,  13,   2,  19,  11,  24,   7],
       [ 12, 123,   9,  18,   3,   9,   8,  11,   7],
       [  5,  12, 148,  10,   4,   6,   8,   5,  11],
       [ 12,  15,   9,  97,   6,  11,   7,  16,  16],
       [  3,   8,  14,  17, 153,   5,   7,   3,   2],
       [ 17,   6,  13,  15,   5, 120,   9,  11,  12],
       [ 11,  11,   8,  12,   5,   5, 134,  10,   2],
       [ 14,  11,   8,  10,   1,   4,   7, 121,  11],
       [ 10,  12,  13,  15,  12,   7,   7,  10,  98]])

In [471]:
w2v_svc_ppl.fit(X_train, Y_train)
w2v_svc_ppl.score(X_test,Y_test)
w2v_predict = w2v_svc_ppl.predict(X_test)
print(metrics.accuracy_score(Y_test, w2v_predict))
print(metrics.classification_report(Y_test, w2v_predict))
print(metrics.cohen_kappa_score(Y_test, w2v_predict))
metrics.confusion_matrix(Y_test, w2v_predict)

[LibSVM]0.862764883956
             precision    recall  f1-score   support

       Arts       0.88      0.89      0.88       133
   Business       0.77      0.81      0.79        95
     Health       0.86      0.87      0.86       119
    Opinion       0.83      0.80      0.82       102
   Politics       0.88      0.89      0.89       112
    Science       0.86      0.82      0.84        99
     Sports       0.97      0.95      0.96       121
      Style       0.88      0.87      0.87       106
 Technology       0.81      0.84      0.82       104

avg / total       0.86      0.86      0.86       991

0.845401185392


array([[118,   2,   0,   4,   1,   1,   0,   6,   1],
       [  2,  77,   1,   3,   0,   2,   1,   2,   7],
       [  0,   3, 103,   2,   3,   5,   0,   2,   1],
       [  6,   4,   5,  82,   2,   1,   0,   0,   2],
       [  1,   2,   4,   2, 100,   1,   0,   0,   2],
       [  1,   2,   4,   3,   1,  81,   0,   1,   6],
       [  1,   1,   0,   2,   0,   0, 115,   1,   1],
       [  5,   3,   2,   0,   0,   2,   1,  92,   1],
       [  0,   6,   1,   1,   6,   1,   1,   1,  87]])

In [327]:
print(w2v_svc_ppl.classes_)

['Arts' 'Business' 'Health' 'Opinion' 'Politics' 'Science' 'Sports' 'Style'
 'Technology']


In [397]:
print([word for word in stopwords.words('english') if word in word2vec])

['i', 'me', 'my', 'myself', 'we', 'our', 'ours', 'ourselves', 'you', 'your', 'yours', 'yourself', 'yourselves', 'he', 'him', 'his', 'himself', 'she', 'her', 'hers', 'herself', 'it', 'its', 'itself', 'they', 'them', 'their', 'theirs', 'themselves', 'what', 'which', 'who', 'whom', 'this', 'that', 'these', 'those', 'am', 'is', 'are', 'was', 'were', 'be', 'been', 'being', 'have', 'has', 'had', 'having', 'do', 'does', 'did', 'doing', 'an', 'the', 'but', 'if', 'or', 'because', 'as', 'until', 'while', 'at', 'by', 'for', 'with', 'about', 'against', 'between', 'into', 'through', 'during', 'before', 'after', 'above', 'below', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over', 'under', 'again', 'further', 'then', 'once', 'here', 'there', 'when', 'where', 'why', 'how', 'all', 'any', 'both', 'each', 'few', 'more', 'most', 'other', 'some', 'such', 'no', 'nor', 'not', 'only', 'own', 'same', 'so', 'than', 'too', 'very', 's', 't', 'can', 'will', 'just', 'don', 'should', 'now', 'd', 'll', 'm', 'o',

In [474]:
fu = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=2000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ])),
    ('w2v', Pipeline([
        ("mean_embedding", MeanEmbeddingVectorizer(word2vec))
    ]))
])

svc_high_ppl = Pipeline([
  ('features', fu),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler(with_mean=True)),
  ('k_best', SelectKBest(score_func=f_classif, k=1800)),
  ('dim_red', PCA(n_components=1500)),
  ('classifier', SVC(kernel='rbf', probability=True, verbose=100, C=1000))
])

In [476]:
svc_high_ppl.fit(X_train[:4000], Y_train[:4000])

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:113: UserWarning:

Features [2020] are constant.

/opt/conda/lib/python3.5/site-packages/sklearn/feature_selection/univariate_selection.py:114: RuntimeWarning:

invalid value encountered in true_divide



[LibSVM]

Pipeline(steps=[('features', FeatureUnion(n_jobs=1,
       transformer_list=[('ngram_tf_idf', Pipeline(steps=[('counts', CountVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_featu...bf',
  max_iter=-1, probability=True, random_state=None, shrinking=True,
  tol=0.001, verbose=100))])

In [477]:
yay_predicted = svc_high_ppl.predict(X_test)

In [478]:
print(metrics.accuracy_score(Y_test, yay_predicted))
print(metrics.classification_report(Y_test, yay_predicted))
print(metrics.cohen_kappa_score(Y_test, yay_predicted))
metrics.confusion_matrix(Y_test, yay_predicted)

0.857719475277
             precision    recall  f1-score   support

       Arts       0.91      0.86      0.88       133
   Business       0.82      0.83      0.83        95
     Health       0.85      0.84      0.85       119
    Opinion       0.83      0.84      0.83       102
   Politics       0.87      0.88      0.88       112
    Science       0.79      0.80      0.79        99
     Sports       0.98      0.98      0.98       121
      Style       0.83      0.87      0.85       106
 Technology       0.81      0.79      0.80       104

avg / total       0.86      0.86      0.86       991

0.839750676637


array([[115,   3,   0,   3,   1,   3,   0,   8,   0],
       [  1,  79,   1,   2,   0,   3,   1,   4,   4],
       [  0,   2, 100,   2,   3,   8,   0,   1,   3],
       [  4,   3,   3,  86,   4,   1,   0,   0,   1],
       [  1,   2,   3,   5,  99,   0,   0,   0,   2],
       [  1,   1,   6,   2,   0,  79,   0,   2,   8],
       [  0,   1,   0,   0,   0,   1, 118,   1,   0],
       [  5,   2,   3,   0,   0,   3,   0,  92,   1],
       [  0,   3,   1,   4,   7,   2,   2,   3,  82]])

In [479]:
fu = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=2000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ])),
    ('w2v', Pipeline([
        ("mean_embedding", MeanEmbeddingVectorizer(word2vec))
    ]))
])

wtwovec = Pipeline([
  ('features', fu),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler(with_mean=True)),
  #('k_best', SelectKBest(score_func=f_classif, k=1800)),
  #('dim_red', PCA(n_components=1500)),
  ('classifier', SVC(kernel='rbf', probability=True, verbose=100, C=1000))
])

In [480]:
wtwovec.fit(X_train[:4000], Y_train[:4000])

[LibSVM]

Pipeline(steps=[('features', FeatureUnion(n_jobs=1,
       transformer_list=[('ngram_tf_idf', Pipeline(steps=[('counts', CountVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_featu...bf',
  max_iter=-1, probability=True, random_state=None, shrinking=True,
  tol=0.001, verbose=100))])

In [481]:
yay2_predicted = wtwovec.predict(X_test)

In [482]:
print(metrics.accuracy_score(Y_test, yay2_predicted))
print(metrics.classification_report(Y_test, yay2_predicted))
print(metrics.cohen_kappa_score(Y_test, yay2_predicted))
metrics.confusion_matrix(Y_test, yay2_predicted)

0.856710393542
             precision    recall  f1-score   support

       Arts       0.90      0.86      0.88       133
   Business       0.80      0.84      0.82        95
     Health       0.89      0.84      0.87       119
    Opinion       0.79      0.82      0.81       102
   Politics       0.85      0.88      0.86       112
    Science       0.79      0.81      0.80        99
     Sports       0.98      0.98      0.98       121
      Style       0.86      0.89      0.87       106
 Technology       0.81      0.77      0.79       104

avg / total       0.86      0.86      0.86       991

0.838630257314


array([[115,   2,   0,   3,   2,   2,   0,   8,   1],
       [  1,  80,   1,   2,   0,   2,   1,   4,   4],
       [  0,   2, 100,   3,   3,   9,   0,   0,   2],
       [  4,   3,   5,  84,   2,   1,   0,   1,   2],
       [  1,   2,   1,   7,  98,   1,   0,   0,   2],
       [  2,   2,   4,   3,   2,  80,   0,   0,   6],
       [  1,   1,   0,   0,   0,   1, 118,   0,   0],
       [  3,   3,   0,   1,   0,   3,   0,  94,   2],
       [  1,   5,   1,   3,   8,   2,   2,   2,  80]])

In [483]:
fu = FeatureUnion([
    ('ngram_tf_idf', Pipeline([
      ('counts', CountVectorizer(max_df=0.75, ngram_range=(1,3), max_features=2000, preprocessor=preprocessor.get_preprocessed_text)),
      ('tf_idf', TfidfTransformer())
    ])),
    ('lv', Pipeline([
      ('linguistic', LinguisticVectorizer())
    ])),
    ('w2v', Pipeline([
        ("mean_embedding", MeanEmbeddingVectorizer(word2vec))
    ]))
])

wtwovec2 = Pipeline([
  ('features', fu),
  ('dense', FunctionTransformer(lambda x: x.todense(), accept_sparse=True)),
  ('scaler', StandardScaler(with_mean=True)),
  #('k_best', SelectKBest(score_func=f_classif, k=1800)),
  #('dim_red', PCA(n_components=1500)),
  ('classifier', SVC(kernel='rbf', probability=True, verbose=100, C=1000))
])

In [ ]:
wtwovec2.fit(X_train, Y_train)

[LibSVM]

Pipeline(steps=[('features', FeatureUnion(n_jobs=1,
       transformer_list=[('ngram_tf_idf', Pipeline(steps=[('counts', CountVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_featu...bf',
  max_iter=-1, probability=True, random_state=None, shrinking=True,
  tol=0.001, verbose=100))])

In [ ]:
yay3_predicted = wtwovec2.predict(X_test)

In [ ]:
print(metrics.accuracy_score(Y_test, yay3_predicted))
print(metrics.classification_report(Y_test, yay3_predicted))
print(metrics.cohen_kappa_score(Y_test, yay3_predicted))
metrics.confusion_matrix(Y_test, yay3_predicted)

0.865792129162
             precision    recall  f1-score   support

       Arts       0.91      0.87      0.89       133
   Business       0.79      0.83      0.81        95
     Health       0.90      0.84      0.87       119
    Opinion       0.82      0.88      0.85       102
   Politics       0.88      0.88      0.88       112
    Science       0.80      0.79      0.79        99
     Sports       0.96      0.98      0.97       121
      Style       0.88      0.90      0.89       106
 Technology       0.82      0.79      0.80       104

avg / total       0.87      0.87      0.87       991

0.848854970586


array([[116,   3,   0,   3,   2,   2,   0,   7,   0],
       [  1,  79,   1,   2,   0,   1,   1,   4,   6],
       [  0,   2, 100,   4,   1,  10,   1,   0,   1],
       [  6,   0,   2,  90,   1,   1,   1,   0,   1],
       [  1,   3,   3,   5,  99,   0,   0,   0,   1],
       [  1,   4,   4,   2,   2,  78,   0,   0,   8],
       [  0,   1,   0,   0,   0,   1, 119,   0,   0],
       [  3,   3,   0,   1,   0,   3,   0,  95,   1],
       [  0,   5,   1,   3,   7,   2,   2,   2,  82]])

In [487]:
word2vec.